In [1]:
pip install fredapi

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [2]:
from fredapi import Fred
import pandas as pd
import numpy as np
import plotly.graph_objects as go
from datetime import datetime
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import date, timedelta
%matplotlib inline
import matplotlib.pyplot as plt
from IPython.core.pylabtools import figsize

fred = Fred(api_key='ff3e047688bbeca011194a522301c33e')

In [3]:
#Indicadores de Actividad Económica
Leading = {}
Leading['CFNAIMA3'] = fred.get_series('CFNAIMA3', observation_start='2010-01-01')
Leading = pd.DataFrame(Leading)

In [4]:
Inflation1 = {}
Inflation1['CPI All'] = fred.get_series('CPIAUCSL', observation_start='2010-01-01', units = 'pc1')
Inflation1['CPI Less Food and Energy'] = fred.get_series('CPILFESL', observation_start='2010-01-01', units = 'pc1')
Inflation1['Underlying Inflation Gauge'] = fred.get_series('UIGFULL', observation_start='2010-01-01') #Inflación persistente
Inflation1['Sticky PriceCPI less Food and Energy'] = fred.get_series('CORESTICKM159SFRBATL', observation_start='2010-01-01')
Inflation1 = pd.DataFrame(Inflation1)
#Perspectivas de Inflación   
Inflation = {}
Inflation['5-Year, 5-Year Forward Inflation Expectation'] = fred.get_series('T5YIFR', observation_start='2010-01-01')
Inflation['5-Year Breakeven Inflation Rate'] = fred.get_series('T5YIE', observation_start='2010-01-01')
Inflation['TIPS Rate'] = fred.get_series('DFII5', observation_start='2010-01-01')
Inflation['Market Yield on U.S. Treasury Securities at 5-Year'] = fred.get_series('DGS5', observation_start='2010-01-01')
                                                        
Inflation = pd.DataFrame(Inflation)

In [5]:
#Real GDP con forecast

rgdp = {}
rgdp['rgdp'] = fred.get_series('GDPC1', observation_start='2015-01-01', units = 'pc1')
rgdp['gdpnow'] = fred.get_series('GDPNOW', observation_start=date.today()- pd.DateOffset(days=90))
rgdp = pd.DataFrame(rgdp)

rgdp1 = {}
rgdp1['FOMC projections'] = fred.get_series('GDPC1CTM', observation_start=date.today())
rgdp1['FOMC projections High'] = fred.get_series('GDPC1RH', observation_start=date.today())
rgdp1['FOMC projections Low'] = fred.get_series('GDPC1RL', observation_start=date.today())

rgdp1 = pd.DataFrame(rgdp1)
rgdp1 = rgdp1.drop(rgdp1.index[0])



In [6]:
rgdp1

FOMC projections  FOMC projections High  FOMC projections Low
2024-01-01              1.50                    2.5                   0.4
2025-01-01              1.80                    2.5                   1.4
2026-01-01              1.85                    2.5                   1.6

In [7]:
#FALTA AGREGAR EN EL CASO DE QUE EL RGDP COINCIDA CON LA FECHA DEL NOWCAST
# Obtener el último valor de rgdp
last_rgdp = rgdp['rgdp'].dropna().iloc[-1]
# Obtener la fecha de la última observación en la columna 'gdpnow'
last_date = rgdp['gdpnow'].index[-1]
# Obtener la fecha anterior
previous_date = last_date - pd.DateOffset(days=91)
# Insertar el valor de last_rgdp en la fecha anterior
rgdp.loc[previous_date, 'gdpnow'] = last_rgdp


In [8]:
#Componentes rgdp

rgdp_comp = {}
rgdp_comp['rgdp'] = fred.get_series('GDPC1', observation_start='2010-01-01')
rgdp_comp['RPCE'] = fred.get_series('PCECC96', observation_start='2010-01-01')
rgdp_comp['RGPDI'] = fred.get_series('GPDIC1', observation_start='2010-01-01')
rgdp_comp['RGCEGI'] = fred.get_series('GCEC1', observation_start='2010-01-01')
rgdp_comp['RNEGS'] = fred.get_series('NETEXC', observation_start='2010-01-01')
rgdp_comp['Residual'] = fred.get_series('AR05RX1Q020SBEA', observation_start='2010-01-01')

rgdp_comp= pd.DataFrame(rgdp_comp)

rgdp_comp1 = {}
rgdp_comp1['rgdp potential'] = fred.get_series('GDPPOT', observation_start='2010-01-01', observation_end=date.today())
rgdp_comp1= pd.DataFrame(rgdp_comp1)



In [9]:
#Contribución a la tasa de crecimeinto del PIB por Industria 
GDPgrowth1 = {}
GDPgrowth1['GDP'] = fred.get_series('CPGDPAI', observation_start='2020-01-01')
GDPgrowth1 = pd.DataFrame(GDPgrowth1)
GDPgrowth1 = GDPgrowth1.tail(1)
GDPgrowth1.index = GDPgrowth1.index.to_period('Q').strftime('%YQ%q')

GDPgrowth = {}
GDPgrowth['Agriculture, Forestry, Fishing'] = fred.get_series('CPGDPAFH', observation_start='2020-01-01')
GDPgrowth['Mining'] = fred.get_series('CPGDPM', observation_start='2020-01-01')
GDPgrowth['Utilities'] = fred.get_series('CPGDPU', observation_start='2020-01-01')
GDPgrowth['Construction'] = fred.get_series('CPGDPC', observation_start='2020-01-01')
GDPgrowth['Manufacturing'] = fred.get_series('CPGDPMA', observation_start='2020-01-01')
GDPgrowth['Wholesale Trade'] = fred.get_series('CPGDPW', observation_start='2020-01-01')
GDPgrowth['Retail Trade'] = fred.get_series('CPGDPR', observation_start='2020-01-01')
GDPgrowth['Transportation and Warehousing'] = fred.get_series('CPGDPT', observation_start='2020-01-01')
GDPgrowth['Information'] = fred.get_series('CPGDPI', observation_start='2020-01-01')
GDPgrowth['Finance, Insurance, Real Estate'] = fred.get_series('CPGDPFIRL', observation_start='2020-01-01')
GDPgrowth['Educational Services, Health Care'] = fred.get_series('CPGDPESHS', observation_start='2020-01-01')
GDPgrowth['Professional and Business Services'] = fred.get_series('CPGDPPBS', observation_start='2020-01-01')
GDPgrowth['Arts, Entertainment, Recreation'] = fred.get_series('CPGDPAERAF', observation_start='2020-01-01')
GDPgrowth['Other Services, Except Government'] = fred.get_series('CPGDPOSEG', observation_start='2020-01-01')
GDPgrowth['Government'] = fred.get_series('CPGDPG', observation_start='2020-01-01')

GDPgrowth= pd.DataFrame(GDPgrowth)
GDPgrowth = GDPgrowth.tail(1)


In [10]:
#Productivity
productivity = {}
productivity['Labor Productivity'] = fred.get_series('OPHNFB', observation_start='2010-01-01', units = 'pc1')
productivity['Hours Worked'] = fred.get_series('HOANBS', observation_start='2010-01-01', units = 'pc1')
productivity['Real Value-Added Output'] = fred.get_series('OUTNFB', observation_start='2010-01-01', units = 'pc1')

productivity = pd.DataFrame(productivity)


In [11]:
#Real Personal Consumption Expenditures
Consumption = {}
Consumption['Services'] = fred.get_series('PCESVC96', observation_start='2010-01-01')
Consumption['Nondurables Goods'] = fred.get_series('PCNDGC96', observation_start='2010-01-01')
Consumption['Durable Goods'] = fred.get_series('PCDGCC96', observation_start='2010-01-01')

Consumption = pd.DataFrame(Consumption)


In [12]:
#Real Personal Income
rpi = {}
rpi['Real Personal Income'] = fred.get_series('RPI', observation_start='2010-01-01')
rpi['RPI excl. tranfers'] = fred.get_series('W875RX1', observation_start='2010-01-01')
rpi['Real Disp. Personal Income'] = fred.get_series('DSPIC96', observation_start='2010-01-01')
rpi['Consumption Expenditures'] = fred.get_series('PCEC96', observation_start='2010-01-01')

rpi = pd.DataFrame(rpi)

In [13]:
#Construction Actvity (Spending)
Construction = {}
Construction['Total Construction'] = fred.get_series('TTLCONS', observation_start='2010-01-01')
Construction['Residential'] = fred.get_series('TLRESCONS', observation_start='2010-01-01')
Construction['Nonresidential'] = fred.get_series('TLNRESCONS', observation_start='2010-01-01')

Construction['Total Construction M/M %'] = fred.get_series('TTLCONS', observation_start='2010-01-01', units = 'pch')
Construction['Residential M/M %'] = fred.get_series('TLRESCONS', observation_start='2010-01-01', units = 'pch')
Construction['Nonresidential M/M %'] = fred.get_series('TLNRESCONS', observation_start='2010-01-01', units = 'pch')

Construction['Total Construction Y/Y %'] = fred.get_series('TTLCONS', observation_start='2010-01-01', units = 'pc1')
Construction['Residential Y/Y %'] = fred.get_series('TLRESCONS', observation_start='2010-01-01', units = 'pc1')
Construction['Nonresidential Y/Y %'] = fred.get_series('TLNRESCONS', observation_start='2010-01-01', units = 'pc1')

Construction = pd.DataFrame(Construction)

In [14]:
#INDUSTRIAL PRODUCTION
Industrial = {}
Industrial['Production Index'] = fred.get_series('INDPRO', observation_start='2010-01-01')
Industrial['Manufacturing (NAICS)'] = fred.get_series('IPMAN', observation_start='2010-01-01')
Industrial['Manufacturing (SIC)'] = fred.get_series('IPMANSICS', observation_start='2010-01-01')
Industrial['Mining'] = fred.get_series('IPMINE', observation_start='2010-01-01') #NAICS =21
Industrial['Utilities: Electric and Gas'] = fred.get_series('IPUTIL', observation_start='2010-01-01') #NAICS = 2211,2


Industrial['Capacity Utilization Index'] = fred.get_series('TCU', observation_start='2010-01-01')
Industrial['Capacity Utilization: Manufacturing(NAICS)'] = fred.get_series('MCUMFN', observation_start='2010-01-01')
Industrial['Capacity Utilization: Mining'] = fred.get_series('CAPUTLG21S', observation_start='2010-01-01')
Industrial['Capacity Utilization: Utilities'] = fred.get_series('CAPUTLG2211A2S', observation_start='2010-01-01')

Industrial['Manufacturers New Orders'] = fred.get_series('AMTMNO', observation_start='2010-01-01', units = 'pch')
Industrial['Invent to Shipmt Ratio'] = fred.get_series('AMTMIS', observation_start='2010-01-01')
Industrial['Inventories to Shipments Ratios: Durable Goods'] = fred.get_series('AMDMIS', observation_start='2010-01-01')
Industrial['Inventories to Shipments Ratios: Nondurable Goods'] = fred.get_series('AMNMIS', observation_start='2010-01-01')

Industrial = pd.DataFrame(Industrial)

In [15]:
#Mercado Laboral 
Labor = {}
Labor['Civilian Labor Force Level'] = fred.get_series('CLF16OV', observation_start='2010-02-02')
Labor['Unemployment Level'] = fred.get_series('UNEMPLOY', observation_start='2010-02-02')
Labor['Job Openings: Total Nonfarm'] = fred.get_series('JTSJOL', observation_start='2010-02-02')
Labor['Employment Level'] = fred.get_series('CE16OV', observation_start='2010-02-02')
Labor['Unemployment Rate'] = fred.get_series('UNRATE', observation_start='2010-02-02')
Labor['Unemployment/Job Openings: Total Nonfarm'] = Labor['Unemployment Level']/Labor['Job Openings: Total Nonfarm']
Labor['Employment Level+Job Openings: Total Nonfarm'] = Labor['Employment Level']+Labor['Job Openings: Total Nonfarm']
Labor = pd.DataFrame(Labor)

In [16]:
#Cuenta Corriente
CurrentAcc = {}
CurrentAcc['Current Account'] = fred.get_series('IEABC', observation_start='2010-02-02')
CurrentAcc['Balance on goods'] = fred.get_series('IEABCG', observation_start='2010-02-02')
CurrentAcc['Balance on services'] = fred.get_series('IEABCS', observation_start='2010-02-02')
CurrentAcc['primary income'] = fred.get_series('IEABCPI', observation_start='2010-02-02')
CurrentAcc['secondary income'] = fred.get_series('IEABCSI', observation_start='2010-02-02')

CurrentAcc = pd.DataFrame(CurrentAcc)

In [17]:
#Trade
Trade = {}
Trade['Exports of goods'] = fred.get_series('BOPGEXP', observation_start='2010-02-02')
Trade['Imports of goods'] = fred.get_series('BOPGIMP', observation_start='2010-02-02')
Trade['Net Exports'] = Trade['Exports of goods']- Trade['Imports of goods']

#Partners
Trade['U.S. Exports of Goods to China'] = fred.get_series('EXPCH', observation_start='2010-02-02')
Trade['U.S. Imports of Goods to China'] = fred.get_series('IMPCH', observation_start='2010-02-02')
Trade['Net Trade to China'] = Trade['U.S. Exports of Goods to China']- Trade['U.S. Imports of Goods to China']

Trade['U.S. Exports of Goods to Mexico'] = fred.get_series('EXPMX', observation_start='2010-02-02')
Trade['U.S. Imports of Goods to Mexico'] = fred.get_series('IMPMX', observation_start='2010-02-02')
Trade['Net Trade to Mexico'] = Trade['U.S. Exports of Goods to Mexico']- Trade['U.S. Imports of Goods to Mexico']

Trade['U.S. Exports of Goods to Canada'] = fred.get_series('EXPCA', observation_start='2010-02-02')
Trade['U.S. Imports of Goods to Canada'] = fred.get_series('IMPCA', observation_start='2010-02-02')
Trade['Net Trade to Canada'] = Trade['U.S. Exports of Goods to Canada']- Trade['U.S. Imports of Goods to Canada']

Trade = pd.DataFrame(Trade)


In [18]:
IIP = {}
IIP['Int Invest Position'] = fred.get_series('IIPUSNETIQ', observation_start='2010-02-02')
IIP['U.S. Assets'] = fred.get_series('IIPUSASSQ', observation_start='2010-02-02')
IIP['U.S.Liabilities'] = fred.get_series('IIPUSLIAQ', observation_start='2010-02-02')

IIP = pd.DataFrame(IIP)


In [19]:
#Financial Activity Measures
finact = {}
finact['NFCI'] = fred.get_series('NFCI', observation_start='2007-02-02')
finact['NFCIRISK'] = fred.get_series('NFCIRISK', observation_start='2007-02-02')
finact['NFCILEVERAGE'] = fred.get_series('NFCILEVERAGE', observation_start='2010-02-02')
finact['NFCICREDIT'] = fred.get_series('NFCICREDIT', observation_start='2010-02-02')
finact = pd.DataFrame(finact)

finact1 = {}
finact1['USEPUINDXM'] = fred.get_series('USEPUINDXM', observation_start='2007-02-02')
finact1['EPUMONETARY'] = fred.get_series('EPUMONETARY', observation_start='2007-02-02')
finact1['EPUGOVTSPEND'] = fred.get_series('EPUGOVTSPEND', observation_start='2007-02-02')
finact1['EMVOVERALLEMV'] = fred.get_series('EMVOVERALLEMV', observation_start='2007-02-02')
finact1 = pd.DataFrame(finact1)

finact2 = {}
finact2['KCFSI'] = fred.get_series('KCFSI', observation_start='2007-02-02')
finact2 = pd.DataFrame(finact2)

finact3 = {}
finact3['STLFSI4'] = fred.get_series('STLFSI4', observation_start='2007-02-02')
finact3 = pd.DataFrame(finact3)




In [20]:
fred = Fred(api_key='857de98cc2c64d68c853aa60efb56688')

In [21]:
YieldC = {}
YieldC['1-Month'] = fred.get_series('DGS1MO', observation_start='2022-01-01', frequency='m')
YieldC['3-Month'] = fred.get_series('DGS3MO', observation_start='2022-01-01', frequency='m')
YieldC['6-Month'] = fred.get_series('DGS6MO', observation_start='2022-01-01', frequency='m')
YieldC['1-Year'] = fred.get_series('DGS1', observation_start='2022-01-01', frequency='m')
YieldC['2-Year'] = fred.get_series('DGS2', observation_start='2022-01-01', frequency='m')
YieldC['3-Year'] = fred.get_series('DGS3', observation_start='2022-01-01', frequency='m')
YieldC['5-Year'] = fred.get_series('DGS5', observation_start='2022-01-01', frequency='m')
YieldC['7-Year'] = fred.get_series('DGS7', observation_start='2022-01-01', frequency='m')
YieldC['10-Year'] = fred.get_series('DGS10', observation_start='2022-01-01', frequency='m')
YieldC['20-Year'] = fred.get_series('DGS20', observation_start='2022-01-01', frequency='m')
YieldC['30-Year'] = fred.get_series('DGS30', observation_start='2022-01-01', frequency='m')

# Convertir a DataFrame y eliminar filas con valores NaN
YieldC = pd.DataFrame(YieldC).dropna()

YieldC1 = {}
YieldC1['1-Month'] = fred.get_series('DGS1MO', observation_start='2023-05-02')
YieldC1['3-Month'] = fred.get_series('DGS3MO', observation_start='2023-05-02')
YieldC1['6-Month'] = fred.get_series('DGS6MO', observation_start='2023-05-02')
YieldC1['1-Year'] = fred.get_series('DGS1', observation_start='2023-05-02')
YieldC1['2-Year'] = fred.get_series('DGS2', observation_start='2023-05-02')
YieldC1['3-Year'] = fred.get_series('DGS3', observation_start='2023-05-02')
YieldC1['5-Year'] = fred.get_series('DGS5', observation_start='2023-05-02')
YieldC1['7-Year'] = fred.get_series('DGS7', observation_start='2023-05-02')
YieldC1['10-Year'] = fred.get_series('DGS10', observation_start='2023-05-02')
YieldC1['20-Year'] = fred.get_series('DGS20', observation_start='2023-05-02')
YieldC1['30-Year'] = fred.get_series('DGS30',observation_start='2023-05-02')
YieldC1 = pd.DataFrame(YieldC1)
YieldC1 = YieldC1.tail(1)

YieldC1

1-Month  3-Month  6-Month  1-Year  2-Year  3-Year  5-Year  7-Year  \
2023-10-13      5.6     5.62     5.57    5.41    5.04     4.8    4.65    4.66   

            10-Year  20-Year  30-Year  
2023-10-13     4.63     4.97     4.78

In [22]:
frames = [YieldC, YieldC1]
YieldCurve = pd.concat(frames)
YieldCurve.index = YieldCurve.index.date

selected_dates = [YieldCurve.index[-4],YieldCurve.index[-3], YieldCurve.index[-2], YieldCurve.index[-1]]
YieldCurve = YieldCurve.loc[selected_dates]
YieldCurve = YieldCurve.transpose()

In [23]:
#Tal vez el VIX YA NO ES NECESARIO
#Financial Markets: Stocks and Bonds
stocks = {}
stocks['SP500'] = fred.get_series('SP500', observation_start='2020-02-01')
stocks['DJIA'] = fred.get_series('DJIA', observation_start='2020-02-01')
stocks['NASDAQCOM'] = fred.get_series('NASDAQCOM', observation_start='2020-02-01')
#stocks['VIX'] = fred.get_series('VIXCLS', observation_start='2020-02-01')

stocks['US High Yield Index Total Return'] = fred.get_series('BAMLHYH0A0HYM2TRIV', observation_start='2020-02-01')
stocks['1-3 Year US Corporate Index Total Return'] = fred.get_series('BAMLCC1A013YTRIV', observation_start='2020-02-01')
stocks['CCC & Lower US High Yield Index Total Return'] = fred.get_series('BAMLHYH0A3CMTRIV', observation_start='2020-02-01')
stocks['Emerging Markets Corporate Plus Index Total Return'] = fred.get_series('BAMLEMCBPITRIV', observation_start='2020-02-01')
stocks = pd.DataFrame(stocks)

#CAMBIO DE BASE 2020-02-01
for column in stocks.columns:
    first_element = stocks[column].iloc[0]  # Obtener el primer elemento de la columna
    stocks[column] = (stocks[column] / first_element) * 100  # Cambiar la base

In [24]:
#Forward Rate and Term premium 
#poner que el average expected rate es por diferencia 
FedFunds = {}
FedFunds['U.S. Treasury Securities at 6-Month'] = fred.get_series('DGS6MO', observation_start='2007-01-01')
FedFunds['U.S. Treasury Securities at 3-Month'] = fred.get_series('DGS3MO', observation_start='2007-01-01')
FedFunds['Fed Funds Target Range - Upper Limit'] = fred.get_series('DFEDTARU', observation_start='2007-01-01')
FedFunds['Fed Funds Target Range - Lower Limit'] = fred.get_series('DFEDTARL', observation_start='2007-01-01')
FedFunds['3-month forward rate, 3 months ahead'] = 100*((((1 + (FedFunds['U.S. Treasury Securities at 6-Month'])/100)**.5)/(1 + (FedFunds['U.S. Treasury Securities at 3-Month'])/100)**.25)**(2)-1)
FedFunds = pd.DataFrame(FedFunds)

TermPremium = {}
TermPremium['Term Premium on a 10 Year'] = fred.get_series('THREEFYTP10', observation_start='2007-01-01', frequency='m')
TermPremium['U.S. Treasury Securities at 10-Year'] = fred.get_series('DGS10', observation_start='2007-01-01', frequency='m')
TermPremium['Average expected short rate'] = TermPremium['U.S. Treasury Securities at 10-Year'] - TermPremium['Term Premium on a 10 Year']
TermPremium  =pd.DataFrame(TermPremium)


In [25]:
#Contrastar con la cuenta de MONETARY AUTHORITY 
FedBalance = {}
#Assets
FedBalance['Total Assets'] = fred.get_series('WALCL', observation_start='2007-01-01')
FedBalance['U.S. Treasury Securities'] = fred.get_series('WSHOTSL', observation_start='2007-01-01')
FedBalance['Mortgage-Backed Securities'] = fred.get_series('WSHOMCB', observation_start='2007-01-01')
FedBalance['Central Bank Liquidity Swaps'] = fred.get_series('SWPT', observation_start='2007-01-01')
FedBalance['Term Asset-Backed Securities Loan Facility (TALF)'] = fred.get_series('H41RESPPAATAL2HNWW', observation_start='2007-01-01')
FedBalance['Liquidity and Credit Facilities: Loans'] = fred.get_series('WLCFLL', observation_start='2007-01-01')
FedBalance['MS Facilities LLC'] = fred.get_series('H41RESPPAAENWW', observation_start='2007-01-01')
FedBalance['Municipal Liquidity Facility'] = fred.get_series('H41RESPPAADHNWW', observation_start='2007-01-01')
FedBalance['Repurchase Agreements'] = fred.get_series('WORAL', observation_start='2007-01-01')
#Liabilities

FedBalance['Total Liabilities'] = fred.get_series('WLTLECL', observation_start='2007-01-01')
FedBalance['Federal Reserve Notes'] = fred.get_series('WLFN', observation_start='2007-01-01')
FedBalance['Reverse Repurchase Agreements'] = fred.get_series('WLRRAL', observation_start='2007-01-01')
FedBalance['Deposits Held by Depository Institutions (Reserves)'] = fred.get_series('WLODLL', observation_start='2007-01-01')
FedBalance['U.S. Treasury, General Account (TGA)'] = fred.get_series('WDTGAL', observation_start='2007-01-01')

FedBalance = pd.DataFrame(FedBalance)
FedBalance['Repo, Swaps, Credit and Liquidity Facilities'] = FedBalance['Central Bank Liquidity Swaps'] + FedBalance['Term Asset-Backed Securities Loan Facility (TALF)'] + FedBalance['Liquidity and Credit Facilities: Loans'] + FedBalance['MS Facilities LLC'] + FedBalance['Municipal Liquidity Facility'] + FedBalance['Repurchase Agreements']
FedBalance['Other Assets'] = FedBalance['Total Assets'] - FedBalance['U.S. Treasury Securities'] - FedBalance['Mortgage-Backed Securities'] - FedBalance['Repo, Swaps, Credit and Liquidity Facilities']
FedBalance['Other Liabilities'] = FedBalance['Total Liabilities'] - FedBalance['Federal Reserve Notes'] - FedBalance['Reverse Repurchase Agreements'] - FedBalance['Deposits Held by Depository Institutions (Reserves)'] - FedBalance['U.S. Treasury, General Account (TGA)'] 

In [26]:
# Lista de columnas a eliminar
columnas_eliminar = ['Central Bank Liquidity Swaps', 'Term Asset-Backed Securities Loan Facility (TALF)',
                     'Liquidity and Credit Facilities: Loans', 'MS Facilities LLC',
                     'Municipal Liquidity Facility', 'Repurchase Agreements']

# Eliminar las columnas del DataFrame
FedBalance.drop(columnas_eliminar, axis=1, inplace=True)


In [27]:
#Debt Outstanding by Intrument and Loans by Instruments QUARTERLY LEVELS, poner una  grafica en niveles apilada
Debt = {}
Debt['Total Debt and Loans'] = fred.get_series('TCMDO', observation_start='2007-01-01')*1000

Debt['Total Loans'] = fred.get_series('ASTLL', observation_start='2007-01-01')
Debt['Loans N.E.C.'] = fred.get_series('FBDILNECA', observation_start='2007-01-01')
Debt['Other Loans and Advances'] = fred.get_series('ASOLAL', observation_start='2007-01-01')
Debt['Mortgages'] = fred.get_series('ASTMA', observation_start='2007-01-01')
Debt['Consumer Credit'] = fred.get_series('CCLBSHNO', observation_start='2007-01-01')*1000

Debt['Total Debt'] = fred.get_series('ASTDSL', observation_start='2007-01-01')
Debt['Open Market Paper'] = fred.get_series('ASOMPL', observation_start='2007-01-01')
Debt['Treasury Securities'] = fred.get_series('FGTSL', observation_start='2007-01-01')
Debt['U.S. Government Agency Securities'] = fred.get_series('ASUSGASL', observation_start='2007-01-01')
Debt['Municipal Securities'] = fred.get_series('DNSMSL', observation_start='2007-01-01')
Debt['Corporate and Foreign Bonds'] = fred.get_series('ASCFBL', observation_start='2007-01-01')

Debt = pd.DataFrame(Debt)


In [28]:
#Debt Outstanding by Intrument and Loans by Instruments QUARTERLY MARKET VALUE, dos subgraficas o ver si las subgraficas es loans- loans
# y Debt - debt (el de face value), o subgrafica de este df debt-loans
Debt1 = {}
Debt1['Total Debt and Loans'] = fred.get_series('TCMDO', observation_start='2007-01-01', units = 'chg')*1000

Debt1['Total Loans'] = fred.get_series('ASTLL', observation_start='2007-01-01', units = 'chg')
Debt1['Loans N.E.C.'] = fred.get_series('FBDILNECA', observation_start='2007-01-01', units = 'chg')
Debt1['Other Loans and Advances'] = fred.get_series('ASOLAL', observation_start='2007-01-01', units = 'chg')
Debt1['Mortgages'] = fred.get_series('ASTMA', observation_start='2007-01-01', units = 'chg')
Debt1['Consumer Credit'] = fred.get_series('CCLBSHNO', observation_start='2007-01-01', units = 'chg')*1000

Debt1['Total Debt'] = fred.get_series('ASTDSL', observation_start='2007-01-01', units = 'chg')
Debt1['Open Market Paper'] = fred.get_series('ASOMPL', observation_start='2007-01-01', units = 'chg')
Debt1['Treasury Securities'] = fred.get_series('FGTSL', observation_start='2007-01-01', units = 'chg')
Debt1['U.S. Government Agency Securities'] = fred.get_series('ASUSGASL', observation_start='2007-01-01', units = 'chg')
Debt1['Municipal Securities'] = fred.get_series('DNSMSL', observation_start='2007-01-01', units = 'chg')
Debt1['Corporate and Foreign Bonds'] = fred.get_series('ASCFBL', observation_start='2007-01-01', units = 'chg')

Debt1 = pd.DataFrame(Debt1)




In [29]:
#Debt Outstanding by Intrument and Loans by Instruments transactions (face value) QUARTERLY
#Creo que es Seasonality adjusted, si hago el cumulative chance pueda recuperar el niver a face value
Debt2 = {}

Debt2['Total Loans'] = fred.get_series('BOGZ1FA894123005Q', observation_start='2007-01-01')
Debt2['Loans N.E.C.'] = fred.get_series('BOGZ1FA793068005Q', observation_start='2007-01-01')
Debt2['Other Loans and Advances'] = fred.get_series('BOGZ1FA893169005Q', observation_start='2007-01-01')
Debt2['Mortgages'] = fred.get_series('BOGZ1FA893065005Q', observation_start='2007-01-01')
Debt2['Consumer Credit'] = fred.get_series('HNOCCLQ027S', observation_start='2007-01-01')

Debt2['Total Debt'] = fred.get_series('BOGZ1FA894122005Q', observation_start='2007-01-01')
Debt2['Open Market Paper'] = fred.get_series('BOGZ1FA893169175Q', observation_start='2007-01-01')
Debt2['Treasury Securities'] = fred.get_series('BOGZ1FA313161105Q', observation_start='2007-01-01')
Debt2['U.S. Government Agency Securities'] = fred.get_series('BOGZ1FA893161705Q', observation_start='2007-01-01')
Debt2['Municipal Securities'] = fred.get_series('BOGZ1FA383162005Q', observation_start='2007-01-01')
Debt2['Corporate and Foreign Bonds'] = fred.get_series('BOGZ1FA893163005Q', observation_start='2007-01-01')

Debt2 = pd.DataFrame(Debt2)



In [30]:
#US TREASURY HOLDERS quarterly levels market value, creo que households incluye hedge funds
Treasury = {}
Treasury['Treasury Levels'] = fred.get_series('BOGZ1FL893061105Q', observation_start='2005-01-01')
Treasury['Households and Nonprofit Organizations'] = fred.get_series('BOGZ1LM153061105Q', observation_start='2005-01-01')
Treasury['Nonfinancial Corporate Business'] = fred.get_series('TSABSNNCB', observation_start='2005-01-01')
Treasury['Nonfinancial Noncorporate Business'] = fred.get_series('TSABSNNB', observation_start='2005-01-01')
Treasury['State and Local Governments'] = fred.get_series('SLGTRSQ027S', observation_start='2005-01-01')
Treasury['Monetary Authority'] = fred.get_series('BOGZ1FL713061103Q', observation_start='2005-01-01')
Treasury['U.S.-Chartered Depository Institutions'] = fred.get_series('BOGZ1LM763061100Q', observation_start='2005-01-01')
Treasury['Foreign Banking Offices in the U.S'] = fred.get_series('BOGZ1LM753061103Q', observation_start='2005-01-01')
Treasury['Banks in U.S.-Affiliated Areas'] = fred.get_series('BOGZ1LM743061103Q', observation_start='2005-01-01')
Treasury['Credit Unions'] = fred.get_series('BOGZ1LM473061105Q', observation_start='2005-01-01')
Treasury['Property-Casualty Insurance Companies'] = fred.get_series('BOGZ1LM513061105Q', observation_start='2005-01-01')
Treasury['Life Insurance Companies'] = fred.get_series('BOGZ1LM543061105Q', observation_start='2005-01-01')
Treasury['Private Pension Funds'] = fred.get_series('BOGZ1LM573061105Q', observation_start='2005-01-01')
Treasury['Federal Government Retirement Funds'] = fred.get_series('BOGZ1LM343061105Q', observation_start='2005-01-01')
Treasury['State and Local Government Employee Defined Benefit'] = fred.get_series('BOGZ1LM223061143Q', observation_start='2005-01-01')
Treasury['Money Market Funds'] = fred.get_series('BOGZ1FL633061105Q', observation_start='2005-01-01')
Treasury['Mutual Funds'] = fred.get_series('BOGZ1LM653061105Q', observation_start='2005-01-01')
Treasury['Closed-End Funds'] = fred.get_series('BOGZ1LM553061103Q', observation_start='2005-01-01')
Treasury['Exchange-Traded Funds'] = fred.get_series('BOGZ1LM563061103Q', observation_start='2005-01-01')
Treasury['Government-Sponsored Enterprises'] = fred.get_series('BOGZ1FL403061105Q', observation_start='2005-01-01')
Treasury['Issuers of Asset-Backed Securities'] = fred.get_series('BOGZ1FL673061103Q', observation_start='2005-01-01')
Treasury['Security Brokers and Dealers'] = fred.get_series('BOGZ1FL663061105Q', observation_start='2005-01-01')
Treasury['Holding Companies'] = fred.get_series('BOGZ1LM733061103Q', observation_start='2005-01-01')
Treasury['Rest of the World'] = fred.get_series('BOGZ1LM263061105Q', observation_start='2005-01-01')

Treasury = pd.DataFrame(Treasury)
Treasury['Household sector'] = Treasury['Households and Nonprofit Organizations']
Treasury['Other nonfinancial'] = Treasury['Nonfinancial Corporate Business'] + Treasury['Nonfinancial Noncorporate Business'] + Treasury['State and Local Governments']
Treasury['Banks'] = Treasury['Holding Companies'] + Treasury['U.S.-Chartered Depository Institutions'] + Treasury['Foreign Banking Offices in the U.S'] + Treasury['Banks in U.S.-Affiliated Areas'] + Treasury['Credit Unions']
Treasury['GSEs'] = Treasury['Government-Sponsored Enterprises']
Treasury['Insurance and pensions'] = Treasury['Property-Casualty Insurance Companies'] + Treasury['Life Insurance Companies'] + Treasury['Private Pension Funds'] + Treasury['Federal Government Retirement Funds'] + Treasury['State and Local Government Employee Defined Benefit']
Treasury['Shadow Banking'] = Treasury['Closed-End Funds'] + Treasury['Exchange-Traded Funds'] + Treasury['Issuers of Asset-Backed Securities'] + Treasury['Security Brokers and Dealers']

columns_delete = ['Households and Nonprofit Organizations', 'Nonfinancial Corporate Business',
                     'Nonfinancial Noncorporate Business', 'State and Local Governments',
                     'Holding Companies', 'U.S.-Chartered Depository Institutions', 'Foreign Banking Offices in the U.S',
                    'Banks in U.S.-Affiliated Areas', 'Credit Unions', 'Government-Sponsored Enterprises', 
                    'Property-Casualty Insurance Companies', 'Life Insurance Companies', 'Private Pension Funds',
                     'Federal Government Retirement Funds', 'State and Local Government Employee Defined Benefit',
                     'Closed-End Funds', 'Exchange-Traded Funds', 'Issuers of Asset-Backed Securities', 'Security Brokers and Dealers']

# Eliminar las columnas del DataFrame
Treasury.drop(columns_delete, axis=1, inplace=True)


In [31]:
#US TREASURY HOLDERS quarterly cambio market value, creo que households incluye hedge funds
Treasury1 = {}
Treasury1['Treasury Transactions'] = fred.get_series('BOGZ1FL893061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Households and Nonprofit Organizations'] = fred.get_series('BOGZ1LM153061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Nonfinancial Corporate Business'] = fred.get_series('TSABSNNCB', observation_start='2005-01-01', units = 'chg')
Treasury1['Nonfinancial Noncorporate Business'] = fred.get_series('TSABSNNB', observation_start='2005-01-01', units = 'chg')
Treasury1['State and Local Governments'] = fred.get_series('SLGTRSQ027S', observation_start='2005-01-01', units = 'chg')
Treasury1['Monetary Authority'] = fred.get_series('BOGZ1FL713061103Q', observation_start='2005-01-01', units = 'chg')
Treasury1['U.S.-Chartered Depository Institutions'] = fred.get_series('BOGZ1LM763061100Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Foreign Banking Offices in the U.S'] = fred.get_series('BOGZ1LM753061103Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Banks in U.S.-Affiliated Areas'] = fred.get_series('BOGZ1LM743061103Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Credit Unions'] = fred.get_series('BOGZ1LM473061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Property-Casualty Insurance Companies'] = fred.get_series('BOGZ1LM513061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Life Insurance Companies'] = fred.get_series('BOGZ1LM543061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Private Pension Funds'] = fred.get_series('BOGZ1LM573061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Federal Government Retirement Funds'] = fred.get_series('BOGZ1LM343061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['State and Local Government Employee Defined Benefit'] = fred.get_series('BOGZ1LM223061143Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Money Market Funds'] = fred.get_series('BOGZ1FL633061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Mutual Funds'] = fred.get_series('BOGZ1LM653061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Closed-End Funds'] = fred.get_series('BOGZ1LM553061103Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Exchange-Traded Funds'] = fred.get_series('BOGZ1LM563061103Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Government-Sponsored Enterprises'] = fred.get_series('BOGZ1FL403061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Issuers of Asset-Backed Securities'] = fred.get_series('BOGZ1FL673061103Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Security Brokers and Dealers'] = fred.get_series('BOGZ1FL663061105Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Holding Companies'] = fred.get_series('BOGZ1LM733061103Q', observation_start='2005-01-01', units = 'chg')
Treasury1['Rest of the World'] = fred.get_series('BOGZ1LM263061105Q', observation_start='2005-01-01', units = 'chg')

Treasury1 = pd.DataFrame(Treasury1)

In [32]:
Treasury1['Household sector'] = Treasury1['Households and Nonprofit Organizations']
Treasury1['Other nonfinancial'] = Treasury1['Nonfinancial Corporate Business'] + Treasury1['Nonfinancial Noncorporate Business'] + Treasury1['State and Local Governments']
Treasury1['Banks'] = Treasury1['Holding Companies'] + Treasury1['U.S.-Chartered Depository Institutions'] + Treasury1['Foreign Banking Offices in the U.S'] + Treasury1['Banks in U.S.-Affiliated Areas'] + Treasury1['Credit Unions']
Treasury1['GSEs'] = Treasury1['Government-Sponsored Enterprises']
Treasury1['Insurance and pensions'] = Treasury1['Property-Casualty Insurance Companies'] + Treasury1['Life Insurance Companies'] + Treasury1['Private Pension Funds'] + Treasury1['Federal Government Retirement Funds'] + Treasury1['State and Local Government Employee Defined Benefit']
Treasury1['Shadow Banking'] = Treasury1['Money Market Funds'] + Treasury1['Mutual Funds'] + Treasury1['Closed-End Funds'] + Treasury1['Exchange-Traded Funds'] + Treasury1['Issuers of Asset-Backed Securities'] + Treasury1['Security Brokers and Dealers']

columns_delete1 = ['Households and Nonprofit Organizations', 'Nonfinancial Corporate Business',
                     'Nonfinancial Noncorporate Business', 'State and Local Governments',
                     'Holding Companies', 'U.S.-Chartered Depository Institutions', 'Foreign Banking Offices in the U.S',
                    'Banks in U.S.-Affiliated Areas', 'Credit Unions', 'Government-Sponsored Enterprises', 
                    'Property-Casualty Insurance Companies', 'Life Insurance Companies', 'Private Pension Funds',
                     'Federal Government Retirement Funds', 'State and Local Government Employee Defined Benefit',
                     'Closed-End Funds', 'Exchange-Traded Funds', 'Issuers of Asset-Backed Securities', 'Security Brokers and Dealers',
                     'Money Market Funds', 'Mutual Funds']

# Eliminar las columnas del DataFrame
Treasury1.drop(columns_delete1, axis=1, inplace=True)

In [34]:
#Transactions
Treasury2 = {}
Treasury2['Treasury Transactions'] = fred.get_series('BOGZ1FA893061105Q', observation_start='2005-01-01')
Treasury2['Households and Nonprofit Organizations'] = fred.get_series('HNOTSBQ027S', observation_start='2005-01-01')
Treasury2['Nonfinancial Corporate Business'] = fred.get_series('NCBTSAQ027S', observation_start='2005-01-01')
Treasury2['Nonfinancial Noncorporate Business'] = fred.get_series('NNBGSAQ027S', observation_start='2005-01-01')
Treasury2['State and Local Governments'] = fred.get_series('SLGTSIQ027S', observation_start='2005-01-01')
Treasury2['Monetary Authority'] = fred.get_series('BOGZ1FA713061103Q', observation_start='2005-01-01')
Treasury2['U.S.-Chartered Depository Institutions'] = fred.get_series('BOGZ1FA763061100Q', observation_start='2005-01-01')
Treasury2['Foreign Banking Offices in the U.S'] = fred.get_series('BOGZ1FA753061103Q', observation_start='2005-01-01')
Treasury2['Banks in U.S.-Affiliated Areas'] = fred.get_series('BOGZ1FA743061103Q', observation_start='2005-01-01')
Treasury2['Credit Unions'] = fred.get_series('BOGZ1FA473061105Q', observation_start='2005-01-01')
Treasury2['Property-Casualty Insurance Companies'] = fred.get_series('BOGZ1FA513061105Q', observation_start='2005-01-01')
Treasury2['Life Insurance Companies'] = fred.get_series('BOGZ1FA543061105Q', observation_start='2005-01-01')
Treasury2['Private Pension Funds'] = fred.get_series('BOGZ1FA573061105Q', observation_start='2005-01-01')
Treasury2['Federal Government Retirement Funds'] = fred.get_series('BOGZ1FA343061105Q', observation_start='2005-01-01')
Treasury2['State and Local Government Employee Defined Benefit'] = fred.get_series('BOGZ1FA223061143Q', observation_start='2005-01-01')
Treasury2['Money Market Funds'] = fred.get_series('BOGZ1FA633061105Q', observation_start='2005-01-01')
Treasury2['Mutual Funds'] = fred.get_series('BOGZ1FA653061105Q', observation_start='2005-01-01')
Treasury2['Closed-End Funds'] = fred.get_series('BOGZ1FA553061103Q', observation_start='2005-01-01')
Treasury2['Exchange-Traded Funds'] = fred.get_series('BOGZ1FA563061103Q', observation_start='2005-01-01')
Treasury2['Government-Sponsored Enterprises'] = fred.get_series('BOGZ1FA403061105Q', observation_start='2005-01-01')
Treasury2['Issuers of Asset-Backed Securities'] = fred.get_series('BOGZ1FA673061103Q', observation_start='2005-01-01')
Treasury2['Security Brokers and Dealers'] = fred.get_series('BOGZ1FA663061105Q', observation_start='2005-01-01')
Treasury2['Holding Companies'] = fred.get_series('BOGZ1FA733061103Q', observation_start='2005-01-01')
Treasury2['Rest of the World'] = fred.get_series('ROWTSAQ027S', observation_start='2005-01-01')

Treasury2 = pd.DataFrame(Treasury2)

In [35]:
Treasury2['Household sector'] = Treasury2['Households and Nonprofit Organizations']
Treasury2['Other nonfinancial'] = Treasury2['Nonfinancial Corporate Business'] + Treasury2['Nonfinancial Noncorporate Business'] + Treasury2['State and Local Governments']
Treasury2['Banks'] = Treasury2['Holding Companies'] + Treasury2['U.S.-Chartered Depository Institutions'] + Treasury2['Foreign Banking Offices in the U.S'] + Treasury2['Banks in U.S.-Affiliated Areas'] + Treasury2['Credit Unions']
Treasury2['GSEs'] = Treasury2['Government-Sponsored Enterprises']
Treasury2['Insurance and pensions'] = Treasury2['Property-Casualty Insurance Companies'] + Treasury2['Life Insurance Companies'] + Treasury2['Private Pension Funds'] + Treasury2['Federal Government Retirement Funds'] + Treasury2['State and Local Government Employee Defined Benefit']
Treasury2['Shadow Banking'] = Treasury2['Money Market Funds'] + Treasury2['Mutual Funds'] + Treasury2['Closed-End Funds'] + Treasury2['Exchange-Traded Funds'] + Treasury2['Issuers of Asset-Backed Securities'] + Treasury2['Security Brokers and Dealers']

columns_delete2 = ['Households and Nonprofit Organizations', 'Nonfinancial Corporate Business',
                     'Nonfinancial Noncorporate Business', 'State and Local Governments',
                     'Holding Companies', 'U.S.-Chartered Depository Institutions', 'Foreign Banking Offices in the U.S',
                    'Banks in U.S.-Affiliated Areas', 'Credit Unions', 'Government-Sponsored Enterprises', 
                    'Property-Casualty Insurance Companies', 'Life Insurance Companies', 'Private Pension Funds',
                     'Federal Government Retirement Funds', 'State and Local Government Employee Defined Benefit',
                     'Closed-End Funds', 'Exchange-Traded Funds', 'Issuers of Asset-Backed Securities', 'Security Brokers and Dealers',
                     'Money Market Funds', 'Mutual Funds']

# Eliminar las columnas del DataFrame
Treasury2.drop(columns_delete2, axis=1, inplace=True)

In [36]:
#YIELD CURVE DE LOS HIGH QUALITY MARKET
HQMBonds = {}
HQMBonds = pd.DataFrame(fred.search_by_release(402))

# Filtrar las series que contienen la frase "Corporate Bond Spot Rate" y un número menor o igual a "30-Year" en la columna 'title'
df_filtered = HQMBonds[HQMBonds['title'].str.contains("Corporate Bond Spot Rate")]

# Ordenar el DataFrame por el número de años en orden ascendente
df = pd.DataFrame(df_filtered['title'])
# Ajustar el ancho de visualización de las columnas
#pd.set_option('display.max_colwidth', None)
#pd.set_option('display.max_rows', None)

# Mostrar el DataFrame
df.sort_values(by='title')

title
series id                                                    
HQMCB1YR    1-Year High Quality Market (HQM) Corporate Bon...
HQMCB1Y6M   1.5-Year High Quality Market (HQM) Corporate B...
HQMCB10YR   10-Year High Quality Market (HQM) Corporate Bo...
HQMCB10Y6M  10.5-Year High Quality Market (HQM) Corporate ...
HQMCB100YR  100-Year High Quality Market (HQM) Corporate B...
...                                                       ...
HQMCB97Y6M  97.5-Year High Quality Market (HQM) Corporate ...
HQMCB98YR   98-Year High Quality Market (HQM) Corporate Bo...
HQMCB98Y6M  98.5-Year High Quality Market (HQM) Corporate ...
HQMCB99YR   99-Year High Quality Market (HQM) Corporate Bo...
HQMCB99Y6M  99.5-Year High Quality Market (HQM) Corporate ...

[200 rows x 1 columns]

In [37]:
# Crear una lista que vaya desde 'HQMCB1YR' hasta 'HQMCB30YR'
series_list = []
for year in range(1, 31):
    series_list.append(f'HQMCB{year}YR')
    series_list.append(f'HQMCB{year}Y6M')
# Agregar 'HQMCB6MT' al inicio de la lista
series_list.insert(0, 'HQMCB6MT')



In [38]:
HQMBond = {}
for series_id in series_list:
    HQMBond[series_id] = fred.get_series(series_id, observation_start='2023-01-01')
    


In [39]:
HQMBond = pd.DataFrame(HQMBond)

In [40]:
HQMBond.index = HQMBond.index.date
selected_dates = [HQMBond.index[-4],HQMBond.index[-3], HQMBond.index[-2], HQMBond.index[-1]]
HQMBond = HQMBond.loc[selected_dates]
HQMBond = HQMBond.transpose()
# Eliminar la última fila del DataFrame
HQMBond.drop(HQMBond.index[-1], inplace=True)

In [41]:
# Importar la biblioteca pandas
import pandas as pd

# Suponiendo que ya tienes el DataFrame HQMBond con los datos proporcionados

# Función para formatear el nombre del índice (nombre de la serie)
def format_series_name(series_id):
    if series_id.endswith('YR'):
        year = series_id.replace('HQMCB', '').replace('YR', '')
        return f"{year}-Year"
    elif series_id.endswith('Y6M'):
        year = series_id.replace('HQMCB', '').replace('Y6M', '')
        return f"{year}.5-Year"
    elif series_id.endswith('B6MT'):
        year = series_id.replace('HQMCB', '').replace('B6MT', '')
        return "6-Months"
    else:
        return series_id

# Renombrar las filas del DataFrame (índice) utilizando la función format_series_name
HQMBond = HQMBond.rename(index=format_series_name)

# Mostrar el DataFrame con los nombres de filas (índice) actualizados
HQMBond


2023-06-01  2023-07-01  2023-08-01  2023-09-01
6-Months         5.73        5.80        5.80        5.85
1-Year           5.60        5.68        5.71        5.79
1.5-Year         5.47        5.57        5.63        5.73
2-Year           5.35        5.46        5.54        5.67
2.5-Year         5.24        5.35        5.45        5.60
3-Year           5.15        5.26        5.37        5.53
3.5-Year         5.07        5.18        5.30        5.47
4-Year           5.01        5.11        5.25        5.42
4.5-Year         4.97        5.07        5.22        5.39
5-Year           4.96        5.05        5.21        5.38
5.5-Year         4.95        5.04        5.21        5.38
6-Year           4.96        5.05        5.22        5.39
6.5-Year         4.98        5.07        5.25        5.42
7-Year           5.01        5.10        5.28        5.45
7.5-Year         5.04        5.13        5.32        5.48
8-Year           5.08        5.16        5.36        5.52
8.5-Year         5.12        5.19        5.39        5.56
9-Year           5.15        5.23        5.43        5.59
9.5-Year         5.18        5.26        5.47        5.62
10-Year          5.22        5.28        5.50        5.65
10.5-Year        5.24        5.31        5.53        5.68
11-Year          5.27        5.33        5.55        5.71
11.5-Year        5.29        5.35        5.58        5.73
12-Year          5.30        5.36        5.59        5.74
12.5-Year        5.32        5.37        5.61        5.75
13-Year          5.33        5.38        5.62        5.76
13.5-Year        5.34        5.38        5.63        5.77
14-Year          5.34        5.38        5.63        5.77
14.5-Year        5.34        5.38        5.63        5.77
15-Year          5.34        5.38        5.63        5.77
15.5-Year        5.34        5.37        5.63        5.77
16-Year          5.34        5.36        5.63        5.77
16.5-Year        5.33        5.35        5.62        5.76
17-Year          5.33        5.35        5.61        5.75
17.5-Year        5.32        5.34        5.61        5.75
18-Year          5.31        5.33        5.60        5.74
18.5-Year        5.31        5.31        5.59        5.73
19-Year          5.30        5.30        5.59        5.72
19.5-Year        5.29        5.29        5.58        5.71
20-Year          5.29        5.28        5.57        5.70
20.5-Year        5.28        5.27        5.56        5.70
21-Year          5.27        5.26        5.55        5.69
21.5-Year        5.26        5.25        5.55        5.68
22-Year          5.26        5.24        5.54        5.67
22.5-Year        5.25        5.23        5.53        5.66
23-Year          5.24        5.22        5.52        5.66
23.5-Year        5.24        5.22        5.52        5.65
24-Year          5.23        5.21        5.51        5.64
24.5-Year        5.23        5.20        5.51        5.64
25-Year          5.22        5.19        5.50        5.63
25.5-Year        5.22        5.19        5.49        5.63
26-Year          5.21        5.18        5.49        5.62
26.5-Year        5.21        5.17        5.49        5.62
27-Year          5.21        5.17        5.48        5.61
27.5-Year        5.20        5.16        5.48        5.61
28-Year          5.20        5.16        5.47        5.61
28.5-Year        5.20        5.15        5.47        5.60
29-Year          5.19        5.15        5.47        5.60
29.5-Year        5.19        5.15        5.46        5.60
30-Year          5.19        5.14        5.46        5.59

In [42]:
#Household debt service ratio 
Debtservice = {}
Debtservice['Household Debt Service'] = fred.get_series('TDSP', observation_start='2007-01-01')
Debtservice['Consumer Debt Service'] = fred.get_series('CDSP', observation_start='2007-01-01')
Debtservice['Mortgage Debt Service'] = fred.get_series('MDSP', observation_start='2007-01-01')

Debtservice = pd.DataFrame(Debtservice)

DebtRatio = {}
DebtRatio['DPI'] =  fred.get_series('DSPI', observation_start='2007-01-01', frequency = 'q', aggregation_method = 'avg')*1000
DebtRatio['Credit Card Debt'] = (fred.get_series('BOGZ1FL153166100Q', observation_start='2007-01-01') / DebtRatio['DPI'])*100
DebtRatio['Auto Loans'] = (fred.get_series('BOGZ1FL153166400Q', observation_start='2007-01-01') / DebtRatio['DPI'])*100
DebtRatio['Student Loans'] = (fred.get_series('BOGZ1FL153166220Q', observation_start='2007-01-01') /DebtRatio['DPI'])*100

DebtRatio = pd.DataFrame(DebtRatio)




In [43]:
#Open Market(Commercial Paper Holders) QUARTERLY LEVElS, este data frame se junta con el de la celda de abajo
#El de Corporate and Foreign Bonds 
ComPaper = {}
ComPaper['Total All Sectors'] = fred.get_series('ASOMPL', observation_start='2007-01-01')
ComPaper['Nonfinancial corporate business'] = fred.get_series('CPABSNNCB', observation_start='2007-01-01')
ComPaper['State and local governments'] = fred.get_series('SLGCOMQ027S', observation_start='2007-01-01')
ComPaper['U.S.-chartered depository institutions'] = fred.get_series('BOGZ1FL763069175Q', observation_start='2007-01-01')
ComPaper['Credit unions'] = fred.get_series('BOGZ1FL473069153Q', observation_start='2007-01-01')
ComPaper['Property-casualty insurance companies'] = fred.get_series('BOGZ1LM513069105Q', observation_start='2007-01-01')
ComPaper['Life insurance companies'] = fred.get_series('BOGZ1LM543069105Q', observation_start='2007-01-01')
ComPaper['Private pension funds'] = fred.get_series('BOGZ1FL573069105Q', observation_start='2007-01-01')
ComPaper['State and local govt. retirement funds'] = fred.get_series('BOGZ1FL223069143Q', observation_start='2007-01-01')
ComPaper['Money market funds'] = fred.get_series('BOGZ1FL633069175Q', observation_start='2007-01-01')
ComPaper['Mutual funds'] = fred.get_series('BOGZ1LM653069100Q', observation_start='2007-01-01')
ComPaper['Government-sponsored enterprises'] = fred.get_series('BOGZ1FL403069105Q', observation_start='2007-01-01')
ComPaper['Brokers and dealers'] = fred.get_series('BOGZ1FL663069103Q', observation_start='2007-01-01')
ComPaper['Funding corporations (other financial)'] = fred.get_series('BOGZ1FL503069105Q', observation_start='2007-01-01')
ComPaper['Rest of the world'] = fred.get_series('BOGZ1LM263069103Q', observation_start='2007-01-01')

ComPaper = pd.DataFrame(ComPaper)
# Rellenar los valores NaN con 0
ComPaper = ComPaper.fillna(0)

In [44]:
#Quarterly Levels, Market Value Corpoarte Bonds 
CorpoBonds = {}
CorpoBonds['Total Bonds'] = fred.get_series('BOGZ1FL893063005Q', observation_start='2007-01-01')
CorpoBonds['Households and Nonprofit'] = fred.get_series('BOGZ1LM153063005Q', observation_start='2007-01-01')
CorpoBonds['Federal Government'] = fred.get_series('FGCBGSQ027S', observation_start='2007-01-01')
CorpoBonds['State and Local Governments'] = fred.get_series('SLGCORQ027S', observation_start='2007-01-01')
CorpoBonds['U.S.-Chartered Depository Institutions'] = fred.get_series('BOGZ1LM763063005Q', observation_start='2007-01-01')
CorpoBonds['Foreign Banking Offices in the U.S'] = fred.get_series('BOGZ1LM753063005Q', observation_start='2007-01-01')
CorpoBonds['Banks in U.S.-Affiliated Areas'] = fred.get_series('BOGZ1LM743063005Q', observation_start='2007-01-01')
CorpoBonds['Credit Unions'] = fred.get_series('BOGZ1LM473063005Q', observation_start='2007-01-01')
CorpoBonds['Property-Casualty Insurance Companies'] = fred.get_series('BOGZ1LM513063005Q', observation_start='2007-01-01')
CorpoBonds['Life Insurance Companies'] = fred.get_series('BOGZ1LM543063005Q', observation_start='2007-01-01')
CorpoBonds['Private Pension Funds'] = fred.get_series('BOGZ1LM573063005Q', observation_start='2007-01-01')
CorpoBonds['Federal Government Retirement Funds'] = fred.get_series('BOGZ1LM343063005Q', observation_start='2007-01-01')
CorpoBonds['State and Local Government Retirement Funds'] = fred.get_series('BOGZ1LM223063045Q', observation_start='2007-01-01')
CorpoBonds['Money Market Funds'] = fred.get_series('BOGZ1FL633063005Q', observation_start='2007-01-01')
CorpoBonds['Mutual Funds'] = fred.get_series('BOGZ1LM653063005Q', observation_start='2007-01-01')
CorpoBonds['Closed-End Funds'] = fred.get_series('BOGZ1LM553063003Q', observation_start='2007-01-01')
CorpoBonds['Exchange-Traded Funds'] = fred.get_series('BOGZ1LM563063003Q', observation_start='2007-01-01')
CorpoBonds['Government-Sponsored Enterprises'] = fred.get_series('BOGZ1FL403063005Q', observation_start='2007-01-01')
CorpoBonds['Finance Companies'] = fred.get_series('BOGZ1LM613063003Q', observation_start='2007-01-01')
CorpoBonds['Real Estate Investment Trusts'] = fred.get_series('BOGZ1FL643063005Q', observation_start='2007-01-01')
CorpoBonds['Security Brokers and Dealers'] = fred.get_series('BOGZ1FL663063005Q', observation_start='2007-01-01')
CorpoBonds['Holding Companies'] = fred.get_series('BOGZ1LM733063003Q', observation_start='2007-01-01')
CorpoBonds['Other Financial Business'] = fred.get_series('BOGZ1FL503063005Q', observation_start='2007-01-01')
CorpoBonds['Rest of the World'] = fred.get_series('BOGZ1LM263063005Q', observation_start='2007-01-01')

CorpoBonds = pd.DataFrame(CorpoBonds)



In [45]:
#Joint DataFrame (suma de commercial paper and Corporate bonds)
#CHECAR QUE AMBOS DATA FRAME VIENEN EN MISMAS UNIDADES DE MEDIDA, IGUAL PARA LAS OTRAS GRAFICAS 
#QUE APARECEN MARKET SHARE
CorporateBonds = {}
CorporateBonds['Total'] = ComPaper['Total All Sectors'] + CorpoBonds['Total Bonds']
CorporateBonds['Household Sector'] = CorpoBonds['Households and Nonprofit']
CorporateBonds['Other nonfinancial'] = ComPaper['Nonfinancial corporate business'] + ComPaper['State and local governments'] + CorpoBonds['State and Local Governments']
CorporateBonds['Fed. Govt.'] = CorpoBonds['Federal Government']
CorporateBonds['Banks'] = ComPaper['U.S.-chartered depository institutions'] + ComPaper['Credit unions'] + CorpoBonds['U.S.-Chartered Depository Institutions'] + CorpoBonds['Foreign Banking Offices in the U.S'] + CorpoBonds['Banks in U.S.-Affiliated Areas'] + CorpoBonds['Credit Unions'] + CorpoBonds['Holding Companies']
CorporateBonds['GSEs'] = ComPaper['Government-sponsored enterprises'] + CorpoBonds['Government-Sponsored Enterprises']
CorporateBonds['Insurance and pensions'] = ComPaper['Property-casualty insurance companies'] + ComPaper['Life insurance companies'] + ComPaper['Private pension funds'] + ComPaper['State and local govt. retirement funds'] + CorpoBonds['Property-Casualty Insurance Companies'] + CorpoBonds['Life Insurance Companies'] + CorpoBonds['Private Pension Funds'] + CorpoBonds['Federal Government Retirement Funds'] + CorpoBonds['State and Local Government Retirement Funds']
CorporateBonds['Shadow Banking'] = ComPaper['Brokers and dealers'] + ComPaper['Funding corporations (other financial)'] + CorpoBonds['Closed-End Funds'] + CorpoBonds['Exchange-Traded Funds'] + CorpoBonds['Finance Companies'] + CorpoBonds['Real Estate Investment Trusts'] + CorpoBonds['Security Brokers and Dealers'] + CorpoBonds['Other Financial Business']
CorporateBonds['Money Market Funds'] = ComPaper['Money market funds'] + CorpoBonds['Money Market Funds']
CorporateBonds['Mutual Funds'] = ComPaper['Mutual funds'] + CorpoBonds['Mutual Funds']
CorporateBonds['Rest of the World'] = ComPaper['Rest of the world'] + CorpoBonds['Rest of the World']

CorporateBonds = pd.DataFrame(CorporateBonds)

In [77]:
#Chicago Fed National Activity Index: Three Month Moving Average (CFNAIMA3)
grafica1 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica1.update_layout(
    title="Chicago Fed National Activity Index: Three Month Moving Average",
    xaxis_title="Fecha",
    yaxis_title="Index"
)

# Configurar el rango del eje x para los últimos 3 años
grafica1.update_layout(
    xaxis_range=[Leading.index[-25], Leading.index[-1]]
)
# Configurar el rango del eje y para los últimos 3 años
min_y = min(Leading[["CFNAIMA3"]].iloc[-25:].min() -.2 )
max_y = max(Leading[["CFNAIMA3"]].iloc[-25:].max() +.2)
grafica1.update_yaxes(fixedrange=False, range=[min_y, max_y])

# Habilitar el control deslizante del rango del eje x
grafica1.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=5, label="5y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    )
)

zero_line = np.zeros(len(Leading))
grafica1.add_trace(go.Scatter(x=Leading.index, y=zero_line, line=dict(color='black', width=0.45), showlegend=False))
# Añadir las tres líneas de la serie de tiempo
grafica1.add_trace(go.Bar(x=Leading.index, y=Leading["CFNAIMA3"], name='CFNAIMA3'))

grafica1.update_layout(dragmode='pan')
# Mostrar la figura
grafica1.show()
#grafica1.write_html("Grafica1.html")

In [47]:
#Inflación
# Create subplots with 1 row and 2 columns
grafica2 = make_subplots(rows=1, cols=2, subplot_titles=("Inflación", "Perspectivas de Inflación"))

# Configure the title 
grafica2.update_layout(title="Datos de Inflación")

# Agregar título al eje Y de la primera subgráfica
grafica2.update_yaxes(title="YoY %", row=1, col=1)

# Agregar título al eje Y de la segunda subgráfica
grafica2.update_yaxes(title="Porcentaje", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica2.update_xaxes(range=[Inflation1.index[-30], Inflation1.index[-1]], row=1, col=1)

# Configurar el rango del eje x para los últimos 3 años en la segunda subgráfica
grafica2.update_xaxes(range=[Inflation.index[-180], Inflation.index[-1]], row=1, col=2)

# Ajustar rango del eje Y para la primera subgráfica
min_y1 = min(Inflation1[["CPI All","CPI Less Food and Energy","Underlying Inflation Gauge","Sticky PriceCPI less Food and Energy"]].iloc[-30:].min() - 0.2)
max_y1 = max(Inflation1[["CPI All","CPI Less Food and Energy","Underlying Inflation Gauge","Sticky PriceCPI less Food and Energy"]].iloc[-30:].max() + 0.2)
grafica2.update_yaxes(fixedrange=False, range=[min_y1, max_y1], row=1, col=1)

# Ajustar rango del eje Y para la segunda subgráfica
min_y2 = min(Inflation[["5-Year, 5-Year Forward Inflation Expectation", "5-Year Breakeven Inflation Rate", "TIPS Rate", "Market Yield on U.S. Treasury Securities at 5-Year"]].iloc[-180:].min() - 0.2)
max_y2 = max(Inflation[["5-Year, 5-Year Forward Inflation Expectation", "5-Year Breakeven Inflation Rate", "TIPS Rate", "Market Yield on U.S. Treasury Securities at 5-Year"]].iloc[-180:].max() + 0.2)
grafica2.update_yaxes(fixedrange=False, range=[min_y2, max_y2], row=1, col=2)

# Enable x-axis range slider for both graphs
grafica2.update_xaxes(rangeslider_visible=True)

# Add the three time series lines to the first graph
grafica2.add_trace(go.Scatter(x=Inflation1.index, y=Inflation1["CPI All"], name="CPI for All Urban Consumers: All Items in U.S. City Average"), row=1, col=1)
grafica2.add_trace(go.Scatter(x=Inflation1.index, y=Inflation1["CPI Less Food and Energy"], name="CPI Less Food and Energy."), row=1, col=1)
grafica2.add_trace(go.Scatter(x=Inflation1.index, y=Inflation1["Underlying Inflation Gauge"], name="Underlying Inflation Gauge", line=dict(color='gray', dash='dot', width =1.5)), row=1, col=1)
grafica2.add_trace(go.Scatter(x=Inflation1.index, y=Inflation1["Sticky PriceCPI less Food and Energy"], name="Sticky Price CPI less Food and Energy"), row=1, col=1)

grafica2.add_trace(go.Scatter(x=Inflation.index, y=Inflation["5-Year, 5-Year Forward Inflation Expectation"], name="5-Year, 5-Year Forward Inflation Expectation Rate"), row=1, col=2)
grafica2.add_trace(go.Scatter(x=Inflation.index, y=Inflation["5-Year Breakeven Inflation Rate"], name="5-Year Breakeven Inflation Rate"), row=1, col=2)
grafica2.add_trace(go.Scatter(x=Inflation.index, y=Inflation["TIPS Rate"], name="Market Yield on U.S. Treasury Securities at 5-Year Inflation-Indexed", line=dict(color='green', dash='solid', width =1.5)), row=1, col=2)
grafica2.add_trace(go.Scatter(x=Inflation.index, y=Inflation["Market Yield on U.S. Treasury Securities at 5-Year"], name="Market Yield on U.S. Treasury Securities at 5-Year", line=dict(color='orangered', dash='solid', width =1.5)), row=1, col=2)


# Update the y-axes and figure configuration
grafica2.update_layout(dragmode='pan')

grafica2.show()

In [48]:
#GDP con Forecast
grafica3 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica3.update_layout(
    title="Real GDP and FOMC Projections",
    xaxis_title="Fecha",
    yaxis_title="Percent Change from Year Ago"
)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica3.update_xaxes(range=[rgdp.index[-10], rgdp1.index[1]])

# Ajustar rango del eje Y
min_y1 = min(rgdp[['rgdp']].iloc[-10:].min() - 2.5)
max_y1 = max(rgdp[['rgdp']].iloc[-10:].max() + 1)
grafica3.update_yaxes(fixedrange=False, range=[min_y1, max_y1])

# Habilitar el control deslizante del rango del eje x
grafica3.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=5, label="5y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    )
)

grafica3.add_trace(go.Scatter(x=rgdp.index, y=rgdp['rgdp'], name='Real GDP'))
grafica3.add_trace(go.Scatter(x=rgdp.index, y=rgdp['gdpnow'], name='GDP Nowcast'))
grafica3.add_trace(go.Scatter(x=rgdp1.index, y=rgdp1['FOMC projections'], name='FOMC Projections Midpoint'))
grafica3.add_trace(go.Scatter(x=rgdp1.index, y=rgdp1['FOMC projections Low'], name='FOMC Projections Low', line=dict(dash='dash', color='gray')))
grafica3.add_trace(go.Scatter(x=rgdp1.index, y=rgdp1['FOMC projections High'], name='FOMC Projections High',line=dict(dash='dash', color='gray')))


grafica3.update_yaxes(fixedrange=False)
grafica3.update_layout(dragmode='pan')
# Mostrar la figura
grafica3.show()

In [49]:
#GDP AND COMPONENTS
# Create subplots with 1 row and 2 columns
grafica4 = make_subplots(rows=1, cols=2, subplot_titles=("Real GDP", "Components of GDP"), column_widths=[0.7, 0.3])

# Configure the title 
grafica4.update_layout(title="GDP and Components")

# Agregar título al eje Y de la primera subgráfica
grafica4.update_yaxes(title="Billions of Chained 2012 Dollars", row=1, col=1)


# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica4.update_xaxes(range=[rgdp_comp1.index[-30], rgdp_comp1.index[-1]], row=1, col=1)

# Obtener el último índice válido de rgdp_comp.index
last_valid_index = rgdp_comp.index.get_loc(rgdp_comp.index[-1], method='pad')


# Obtener las fechas de rgdp_comp.index y formatear el mes y el año
fechas_formateadas = rgdp_comp.index.strftime("%b %Y")

# Convertir las fechas formateadas a objetos datetime
fechas_datetime = [datetime.strptime(fecha, "%b %Y") for fecha in fechas_formateadas]

# Configurar el rango del eje x para los últimos años en la segunda subgráfica
grafica4.update_xaxes(range=[rgdp_comp.index[last_valid_index], rgdp_comp.index[last_valid_index]], 
                      tickvals=fechas_datetime, 
                      ticktext=fechas_formateadas, 
                      row=1, col=2)

# Enable x-axis range slider for both graphs
grafica4.update_xaxes(rangeslider_visible=True, row=1, col=1)

# Add the three time series lines to the first graph
grafica4.add_trace(go.Scatter(x=rgdp_comp.index, y=rgdp_comp["rgdp"], name="Real GDP"), row=1, col=1)
grafica4.add_trace(go.Scatter(x=rgdp_comp1.index, y=rgdp_comp1["rgdp potential"], name="Potential Real GDP", line=dict(dash='dash', color='red')), row=1, col=1)

grafica4.add_trace(go.Bar(x=rgdp_comp.index, y=rgdp_comp["RPCE"], texttemplate="Personal Consumption Expenditures", offsetgroup=1, textposition = "inside", showlegend=False), row=1, col=2)
grafica4.add_trace(go.Bar(x=rgdp_comp.index, y=rgdp_comp["RGPDI"], texttemplate="Gross Private Domestic Investment", offsetgroup=1, textposition = "inside", showlegend=False), row=1, col=2)
grafica4.add_trace(go.Bar(x=rgdp_comp.index, y=rgdp_comp["RGCEGI"], texttemplate="Government Consumption Expenditures", offsetgroup=1, textposition = "inside", showlegend=False), row=1, col=2)
grafica4.add_trace(go.Bar(x=rgdp_comp.index, y=rgdp_comp["RNEGS"], texttemplate="Net Exports of Goods and Services", offsetgroup=1, textposition = "inside", showlegend=False), row=1, col=2)
grafica4.add_trace(go.Bar(x=rgdp_comp.index, y=rgdp_comp["Residual"], texttemplate="Residual", offsetgroup=1, textposition = "inside", showlegend=False), row=1, col=2)
grafica4.update_layout(barmode='relative')

grafica4.update_yaxes(fixedrange=False)
grafica4.update_layout(dragmode='pan')

grafica4.show()

C:\Users\J19167\AppData\Local\Temp\ipykernel_7576\3059962087.py:16: FutureWarning:

Passing method to DatetimeIndex.get_loc is deprecated and will raise in a future version. Use index.get_indexer([item], method=...) instead.



In [50]:
GDPgrowth1

GDP
2023Q1  2.0

In [51]:
#FALTA AGREGAR PARA QUE ES TASAS ANUALES SEASONALLY ADJUSTED Y VER SI MEJOR QUITO GDP
# Crear la figura de la gráfica de barras horizontales
grafica5 = go.Figure()

# Obtener los nombres de las industrias
industrias = GDPgrowth.columns.tolist()

# Obtener los porcentajes de crecimiento del PIB
porcentajes = GDPgrowth.values.flatten()


# Crear un DataFrame auxiliar para ordenar los datos
df_aux = pd.DataFrame({'Industria': industrias, 'Porcentaje': porcentajes})
df_aux = df_aux.sort_values(by='Porcentaje', ascending=False)

# Obtener los datos ordenados
industrias_ordenadas = df_aux['Industria'].tolist()
porcentajes_ordenados = df_aux['Porcentaje'].tolist()

# Crear una lista de colores basada en los valores de porcentaje
colores = ['mediumslateblue' if p >= 0 else 'red' for p in porcentajes_ordenados]


# Agregar las barras horizontales
grafica5.add_trace(go.Bar(
    y=industrias_ordenadas[::-1],  # Invertir el orden de las industrias
    x=porcentajes_ordenados[::-1],  # Invertir el orden de los porcentajes
    orientation='h',
    marker=dict(color=colores[::-1]),  # Invertir el orden de los colores
    text=porcentajes_ordenados[::-1],  # Invertir el orden de los porcentajes en el texto
    textposition='inside',
    hovertemplate='Industria: %{y}<br>Porcentaje: %{x}%<extra></extra>'
))

# Configurar el diseño de la figura
grafica5.update_layout(
    title=f'Contribución a la tasa de crecimiento del PIB Real por Industria \
    <br> Real GDP Growth {GDPgrowth1.index[0]}: {GDPgrowth1["GDP"].iloc[0]} %',
    xaxis_title='Porcentaje',
    yaxis_title='Industria',
     plot_bgcolor='whitesmoke',
    bargap=0.1,
    bargroupgap=0.1,
    height=700, #eliminar al protear en html
    width=1400, #eliminar al protear en html
    xaxis=dict(
        range=[min(porcentajes_ordenados) - .2, max(porcentajes_ordenados) + .2]  # Establecer el rango manualmente
    )
)
grafica5.update_layout(dragmode='pan')
# Mostrar la gráfica
grafica5.show()

In [52]:
#Grafica de productividad 
grafica6 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica6.update_layout(
    title="Productivity",
    xaxis_title="Fecha",
    yaxis_title="Percent Change from Year Ago"
)

# Configurar el rango del eje x para los últimos 3 años
grafica6.update_layout(
    xaxis_range=[productivity.index[-25], productivity.index[-1]]
)
# Configurar el rango del eje y para los últimos 3 años
min_y = min(productivity[["Labor Productivity","Hours Worked","Real Value-Added Output"]].iloc[-25:].min() -.8 )
max_y = max(productivity[["Labor Productivity","Hours Worked","Real Value-Added Output"]].iloc[-25:].max() +.8)
grafica6.update_yaxes(fixedrange=False, range=[min_y, max_y])

# Habilitar el control deslizante del rango del eje x
grafica6.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=5, label="5y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    )
)


grafica6.add_trace(go.Scatter(x=productivity.index, y=productivity["Labor Productivity"], name='Nonfarm Business Sector: Labor Productivity (Output per Hour)'))
grafica6.add_trace(go.Scatter(x=productivity.index, y=productivity["Hours Worked"], name='Nonfarm Business Sector: Hours Worked for All Workers'))
grafica6.add_trace(go.Scatter(x=productivity.index, y=productivity["Real Value-Added Output"], name='Nonfarm Business Sector: Real Value-Added Output for All Workers'))

grafica6.update_layout(dragmode='pan')
# Mostrar la figura
grafica6.show()


In [53]:
#Grafica Real Personal Consumption Expenditures 
grafica7 = make_subplots(specs=[[{"secondary_y": True}]])

# Configurar el título y los títulos de los ejes x e y
grafica7.update_layout(
    title="Real Personal Consumption Expenditures",
    xaxis_title="Fecha",
    yaxis_title="Billions of Chained 2012 Dollars"
)

# Configurar el rango del eje x para los últimos 3 años
grafica7.update_layout(xaxis_range=[Consumption.index[-25], Consumption.index[-1]])

# Habilitar el control deslizante del rango del eje x
grafica7.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=5, label="5y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    )
)


grafica7.add_trace(go.Scatter(x=Consumption.index, y=Consumption["Services"], name='Services  (LEFT)'))
grafica7.add_trace(go.Scatter(x=Consumption.index, y=Consumption["Nondurables Goods"], name='Nondurables Goods  (RIGHT)'), secondary_y=True)
grafica7.add_trace(go.Scatter(x=Consumption.index, y=Consumption["Durable Goods"], name='Durable Goods  (RIGHT)'), secondary_y=True)

grafica7.update_yaxes(fixedrange=False)
grafica7.update_layout(dragmode='pan')
# Mostrar la figura
grafica7.show()

In [54]:
#Grafica PERSONAL INCOME AND CONSUMPTION
grafica8 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica8.update_layout(
    title="Income and Consumption",
    xaxis_title="Fecha",
    yaxis_title="Billions of Chained 2012 Dollars"
)

# Configurar el rango del eje x para los últimos 3 años
grafica8.update_layout(
    xaxis_range=[rpi.index[-42], rpi.index[-1]]
)
# Configurar el rango del eje y para los últimos 3 años
min_y = min(rpi[["Real Personal Income","RPI excl. tranfers","Real Disp. Personal Income","Consumption Expenditures"]].iloc[-42:].min() -300 )
max_y = max(rpi[["Real Personal Income","RPI excl. tranfers","Real Disp. Personal Income","Consumption Expenditures"]].iloc[-42:].max() +300)
grafica8.update_yaxes(fixedrange=False, range=[min_y, max_y])

# Habilitar el control deslizante del rango del eje x
grafica8.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=5, label="5y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    )
)


grafica8.add_trace(go.Scatter(x=rpi.index, y=rpi["Real Personal Income"], name='Real Personal Income'))
grafica8.add_trace(go.Scatter(x=rpi.index, y=rpi["RPI excl. tranfers"], name='RPI excl. tranfers'))
grafica8.add_trace(go.Scatter(x=rpi.index, y=rpi["Real Disp. Personal Income"], name='Real Disp. Personal Income'))
grafica8.add_trace(go.Scatter(x=rpi.index, y=rpi["Consumption Expenditures"], name='Consumption Expenditures'))

grafica8.update_layout(dragmode='pan')
# Mostrar la figura
grafica8.show()

In [55]:
#GRAFICA DE CONSTRUCCIÓN FALTA DARLE FORMATO A LOS NOMBRES 
grafica9 = make_subplots(rows=1, cols=3, subplot_titles=("Construction: Levels", "Month-to-Month % Change", "Year-over-Year % Change"))

# Configure the title 
grafica9.update_layout(title="Construction Spending")

# Agregar título al eje Y 
grafica9.update_yaxes(title="Millions of Dollars", row=1, col=1)
grafica9.update_yaxes(title="M\M % Change", row=1, col=2)
grafica9.update_yaxes(title="Y\Y % Change", row=1, col=3)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica9.update_xaxes(range=[Construction.index[-26], Construction.index[-1]])
grafica9.update_yaxes(fixedrange=False)

# Ajustar rango del eje Y para la primera subgráfica
min_y1 = min(Construction[["Total Construction M/M %","Residential M/M %","Nonresidential M/M %"]].iloc[-26:].min() - 1)
max_y1 = max(Construction[["Total Construction M/M %","Residential M/M %","Nonresidential M/M %"]].iloc[-26:].max() + 1)
grafica9.update_yaxes(fixedrange=False, range=[min_y1, max_y1], row=1, col=2)

# Ajustar rango del eje Y para la segunda subgráfica
min_y2 = min(Construction[["Total Construction Y/Y %", "Residential Y/Y %", "Nonresidential Y/Y %"]].iloc[-26:].min() - 4)
max_y2 = max(Construction[["Total Construction Y/Y %", "Residential Y/Y %", "Nonresidential Y/Y %"]].iloc[-26:].max() + 4)
grafica9.update_yaxes(fixedrange=False, range=[min_y2, max_y2], row=1, col=3)


# Add the three time series lines to the first graph
grafica9.add_trace(go.Scatter(x=Construction.index, y=Construction["Total Construction"], name="Total Construction", line=dict(dash='solid', color='purple')), row=1, col=1)
grafica9.add_trace(go.Bar(x=Construction.index, y=Construction["Residential"], name="Residential", offsetgroup=0, marker_color = "dodgerblue"), row=1, col=1)
grafica9.add_trace(go.Bar(x=Construction.index, y=Construction["Nonresidential"], name="Nonresidential", offsetgroup=0, marker_color="red"), row=1, col=1)
grafica9.update_layout(barmode='relative')

grafica9.add_trace(go.Scatter(x=Construction.index, y=Construction["Total Construction M/M %"], name="Total Construction M/M %", line=dict(dash='solid', color='purple'), showlegend=False), row=1, col=2)
grafica9.add_trace(go.Scatter(x=Construction.index, y=Construction["Residential M/M %"], name="Residential M/M %", line=dict(dash='solid', color='dodgerblue'), showlegend=False), row=1, col=2)
grafica9.add_trace(go.Scatter(x=Construction.index, y=Construction["Nonresidential M/M %"], name="Nonresidential M/M %", line=dict(dash='solid', color='red'), showlegend=False), row=1, col=2)

grafica9.add_trace(go.Scatter(x=Construction.index, y=Construction["Total Construction Y/Y %"], name="Total Construction Y/Y %", line=dict(dash='solid', color='purple'), showlegend=False), row=1, col=3)
grafica9.add_trace(go.Scatter(x=Construction.index, y=Construction["Residential Y/Y %"], name="Residential Y/Y %", line=dict(dash='solid', color='dodgerblue'), showlegend=False), row=1, col=3)
grafica9.add_trace(go.Scatter(x=Construction.index, y=Construction["Nonresidential Y/Y %"], name="Nonresidential Y/Y %", line=dict(dash='solid', color='red'), showlegend=False), row=1, col=3)

grafica9.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica9.update_layout(dragmode='pan')

grafica9.show()


In [56]:
#GRAFICA 10 MANUFACTURAS
grafica10 = make_subplots(rows=1, cols=2, subplot_titles=("Industrial Production and Industry Group", "Capacity Utilization %"))

# Configure the title 
grafica10.update_layout(title="Industrial Production and Capacity Utilization")

# Agregar título al eje Y 
grafica10.update_yaxes(title="Index(2017 = 100)", row=1, col=1)
grafica10.update_yaxes(title="% of capacity", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica10.update_xaxes(range=[Industrial.index[-41], Industrial.index[-1]])
grafica10.update_yaxes(fixedrange=False)


# Add the three time series lines to the first graph
grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Production Index"], name="Total Production Index", line=dict(dash='solid', color='black', width=4)), row=1, col=1)
grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Manufacturing (NAICS)"], name="Manufacturing (NAICS)", line=dict(dash='solid', color='red', width=1.5)), row=1, col=1)
grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Mining"], name="Mining", line=dict(dash='solid', color='green', width=1.5)), row=1, col=1)
grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Utilities: Electric and Gas"], name="Utilities: Electric and Gas", line=dict(dash='solid', color='orange', width=1.5)), row=1, col=1)

grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Capacity Utilization Index"], name="Capacity Utilization:Total Index", line=dict(dash='solid', color='black', width=4), showlegend=False), row=1, col=2)
grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Capacity Utilization: Manufacturing(NAICS)"], name="Capacity Utilization: Manufacturing(SIC)", line=dict(dash='solid', color='red', width=1.5), showlegend=False), row=1, col=2)
grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Capacity Utilization: Mining"], name="Capacity Utilization: Mining", line=dict(dash='solid', color='green', width=1.5), showlegend=False), row=1, col=2)
grafica10.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Capacity Utilization: Utilities"], name="Capacity Utilization: Utilities", line=dict(dash='solid', color='orange', width=1.5), showlegend=False), row=1, col=2)


grafica10.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica10.update_layout(dragmode='pan')

grafica10.show()


In [57]:
#GRAFICA 11 MANUFACTURAS
grafica11 = make_subplots(rows=1, cols=2, subplot_titles=("Manufacturers' New Orders", "Inventory/Shipments Ratio"))

# Configure the title 
grafica11.update_layout(title="Manufacturing")

# Agregar título al eje Y 
grafica11.update_yaxes(title="Month-to-Month % Change", row=1, col=1)
grafica11.update_yaxes(title="Ratio", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica11.update_xaxes(range=[Industrial.index[-41], Industrial.index[-1]])
grafica11.update_xaxes(range=[Industrial.index[-15], Industrial.index[-1]],row=1, col=1 )

# Ajustar rango del eje Y para la primera subgráfica
min_y1 = min(Industrial[["Manufacturers New Orders"]].iloc[-15:].min() - .5)
max_y1 = max(Industrial[["Manufacturers New Orders"]].iloc[-15:].max() + .5)
grafica11.update_yaxes(fixedrange=False, range=[min_y1, max_y1], row=1, col=1)

grafica11.update_yaxes(fixedrange=False)

# Add the three time series lines to the first graph
grafica11.add_trace(go.Bar(x=Industrial.index, y=Industrial["Manufacturers New Orders"], name="Manufacturers' New Orders", text = Industrial["Manufacturers New Orders"], textposition="inside"), row=1, col=1)

grafica11.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Invent to Shipmt Ratio"], name="Inventories to Shipments Ratio: Total"), row=1, col=2)
grafica11.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Inventories to Shipments Ratios: Durable Goods"], name="Inventories to Shipments Ratios: Durable Goods"), row=1, col=2)
grafica11.add_trace(go.Scatter(x=Industrial.index, y=Industrial["Inventories to Shipments Ratios: Nondurable Goods"], name="Inventories to Shipments Ratios: Nondurable Goods"), row=1, col=2)

grafica11.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica11.update_layout(dragmode='pan')

grafica11.show()


In [58]:
#Labor Market gráfica 12
#OJO COMO QUE NO CUENTAN LA MISMA HISTORIA, EN UNA DICES QUE EL MERCADO ESTA FULL 
#Y EN LA SEGUNDA DICES QUE HAY MÁS DEMANDA DE TRABAJO QUE OFERTA (DEBERÍA HABER MÁS VACANTES). O CHANCE SI CUENTA LO MISMO
#QUE EL MERCADO LABORAL ESTÁ FULL EMPLOYMENT
grafica12 = make_subplots(rows=1, cols=2, subplot_titles=("Labor Market Tightness: Vacancies per Unemployed Person", "Labor Supply and Labor Demand"))

# Configure the title 
grafica12.update_layout(title="Labor Market")

# Agregar título al eje Y 
grafica12.update_yaxes(title="Ratio", row=1, col=1)
grafica12.update_yaxes(title="Thousands of Person", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica12.update_xaxes(range=[Labor.index[-41], Labor.index[-1]])

grafica12.update_yaxes(fixedrange=False)

# Ajustar margen inferior para dejar espacio para la anotación
grafica12.update_layout(margin=dict(b=123))

# Add the three time series lines to the first graph
grafica12.add_trace(go.Scatter(x=Labor.index, y=Labor["Unemployment/Job Openings: Total Nonfarm"], name="Unemployment/Job Openings: Total Nonfarm"), row=1, col=1)
grafica12.add_trace(go.Scatter(x=Labor.index, y=Labor['Unemployment Rate'], name="Unemployment Rate"), row=1, col=1)

grafica12.add_trace(go.Scatter(x=Labor.index, y=Labor["Civilian Labor Force Level"], name="Civilian Labor Force Level"), row=1, col=2)
grafica12.add_trace(go.Scatter(x=Labor.index, y=Labor["Employment Level+Job Openings: Total Nonfarm"], name="Employment Level+Job Openings: Total Nonfarm"), row=1, col=2)

grafica12.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica12.update_layout(dragmode='pan')

grafica12.show()



In [59]:
#Grafica 13 US Current-Account and Component Balances
grafica13 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica13.update_layout(
    title="US Current-Account and Component Balances",
    xaxis_title="Fecha",
    yaxis_title="Millions of Dollars",
    plot_bgcolor="white"
)


# Añadir las tres líneas de la serie de tiempo
grafica13.add_trace(go.Bar(x=CurrentAcc.index, y=CurrentAcc["Balance on goods"], name="Balance on goods", marker_color='lightgrey', offsetgroup=0))
grafica13.add_trace(go.Bar(x=CurrentAcc.index, y=CurrentAcc["Balance on services"], name="Balance on services", marker_color='darkblue', offsetgroup=0))
grafica13.add_trace(go.Bar(x=CurrentAcc.index, y=CurrentAcc["primary income"], name="Primary Income", marker_color='lightskyblue', offsetgroup=0))
grafica13.add_trace(go.Bar(x=CurrentAcc.index, y=CurrentAcc["secondary income"], name="Secondary Income", marker_color='gold', offsetgroup=0))
grafica13.add_trace(go.Line(x=CurrentAcc.index, y=CurrentAcc["Current Account"], name="Current Account Balance", marker_color ='orangered'))

grafica13.update_layout(barmode='relative')
grafica13.update_xaxes(rangeslider_visible=True)
grafica13.update_yaxes(fixedrange=False, autorange=True)
grafica13.update_layout(dragmode='pan')


# Mostrar la figura
grafica13.show()

D:\devenv\Anaconda32022.05\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [60]:
#Trade gráfica 14
#OJO LA SERIE DE CHINA PARECE QUE HAY SEASONALLITY
#falta poner d enegro la linea de cero de la segunda subgrafica
grafica14 = make_subplots(rows=1, cols=2, subplot_titles=("Overall trade in goods", "Trade Balance of Goods with partners"))

# Configure the title 
grafica14.update_layout(title="International Trade")

# Agregar título al eje Y 
grafica14.update_yaxes(title="Millions of Dollars", row=1, col=1)
grafica14.update_yaxes(title="Millions of Dollars", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica14.update_xaxes(range=[Trade.index[-41], Trade.index[-1]])

grafica14.update_yaxes(fixedrange=False)


# Add the three time series lines to the first graph
grafica14.add_trace(go.Bar(x=Trade.index, y=Trade["Exports of goods"], name="Exports of goods", offsetgroup=0), row=1, col=1)
grafica14.add_trace(go.Bar(x=Trade.index, y=-Trade["Imports of goods"], name="Imports of goods", offsetgroup=0), row=1, col=1)
grafica14.add_trace(go.Scatter(x=Trade.index, y=Trade["Net Exports"], name="Net Exports", marker_color='black'), row=1, col=1)
grafica14.update_layout(barmode='relative')

grafica14.add_trace(go.Scatter(x=Trade.index, y=Trade["Net Trade to China"], name="Net Trade to China"), row=1, col=2)
grafica14.add_trace(go.Scatter(x=Trade.index, y=Trade["Net Trade to Mexico"], name="Net Trade to Mexico"), row=1, col=2)
grafica14.add_trace(go.Scatter(x=Trade.index, y=Trade["Net Trade to Canada"], name="Net Trade to Canada"), row=1, col=2)

zero_line = np.zeros(len(Trade))
grafica14.add_trace(go.Scatter(x=Trade.index, y=zero_line, line=dict(color='black', width=0.50), showlegend=False), row=1, col=2)

grafica14.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica14.update_layout(dragmode='pan')

grafica14.show()

In [61]:
#Grafica 15 U.S. International Investment Position
#Verificar que sea at the end of the Quarter
grafica15 = make_subplots(specs=[[{"secondary_y": True}]])

# Configurar el título y los títulos de los ejes x e y
grafica15.update_layout(
    title="U.S. International Investment Position",
    xaxis_title="Fecha",
    yaxis_title="Millions of Dollars",
    plot_bgcolor="whitesmoke"
)

# Configurar el rango del eje x para los últimos 3 años
grafica15.update_layout(xaxis_range=[IIP.index[-25], IIP.index[-1]])

# Habilitar el control deslizante del rango del eje x
grafica15.update_xaxes(
    rangeslider_visible=True,
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(count=1, label="YTD", step="year", stepmode="todate"),
            dict(count=1, label="1y", step="year", stepmode="backward"),
            dict(count=5, label="5y", step="year", stepmode="backward"),
            dict(step="all")
        ])
    )
)


grafica15.add_trace(go.Scatter(x=IIP.index, y=IIP["Int Invest Position"], name='Net Int. Invest. Position'))
grafica15.add_trace(go.Scatter(x=IIP.index, y=IIP["U.S. Assets"], name='U.S. Assets', marker_color ='darkblue'))
grafica15.add_trace(go.Scatter(x=IIP.index, y=IIP["U.S.Liabilities"], name='U.S.Liabilities', marker_color ='orangered'))

zero_line = np.zeros(len(IIP))
grafica15.add_trace(go.Scatter(x=IIP.index, y=zero_line, line=dict(color='black', width=0.40), showlegend=False))

grafica15.update_yaxes(fixedrange=False)
grafica15.update_layout(dragmode='pan')
# Mostrar la figura
grafica15.show()

**Variables Financieras U.S.**

In [62]:
#Grafica 16 Financial Conditions Indices
grafica16 = make_subplots(rows=1, cols=2,specs=[[{"secondary_y": True}, {"secondary_y": True}]], subplot_titles=("U.S. Financial Conditions", "Economic Policy Uncertainty"))

# Configure the title 
grafica16.update_layout(title="Financial Conditions")

# Agregar título al eje Y 
grafica16.update_yaxes(title="Index", row=1, col=1)
grafica16.update_yaxes(title="Index", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica16.update_xaxes(range=[finact.index[-55], finact.index[-1]])
grafica16.update_xaxes(range=[finact1.index[-20], finact.index[-1]], row=1, col=2)

min_y1 = np.minimum(finact["NFCI"].iloc[-55:].min(), finact3["STLFSI4"].iloc[-55:].min()) - .3
max_y1 = np.maximum(finact["NFCI"].iloc[-55:].max(), finact3["STLFSI4"].iloc[-55:].max()) + .3
grafica16.update_yaxes(fixedrange=False, range=[min_y1, max_y1], row=1, col=1)



# Ajustar rango del eje Y para la segunda subgráfica
min_y2 = min(finact1[["USEPUINDXM", "EPUMONETARY", "EPUGOVTSPEND"]].iloc[-20:].min() - 20)
max_y2 = max(finact1[["USEPUINDXM", "EPUMONETARY", "EPUGOVTSPEND"]].iloc[-20:].max() + 20)
grafica16.update_yaxes(fixedrange=False, range=[min_y2, max_y2], row=1, col=2, secondary_y = False)


grafica16.update_yaxes(fixedrange=False)


# Add the three time series lines to the first graph
grafica16.add_trace(go.Scatter(x=finact2.index, y=finact2["KCFSI"], name="Kansas City Financial Stress Index (Right)"), secondary_y=True, row=1, col=1)
grafica16.add_trace(go.Scatter(x=finact.index, y=finact["NFCI"], name="Chicago Fed National Financial Conditions Index"), row=1, col=1)
grafica16.add_trace(go.Scatter(x=finact3.index, y=finact3["STLFSI4"], name="St. Louis Fed Financial Stress Index"), row=1, col=1)
zero_line = np.zeros(len(finact3))
grafica16.add_trace(go.Scatter(x=finact3.index, y=zero_line, line=dict(color='black', width=0.40), showlegend=False), row=1, col=1)

grafica16.add_trace(go.Scatter(x=finact1.index, y=finact1["USEPUINDXM"], name="Economic Policy Uncertainty Index for United States (US EPU)", line=dict(color='black')), row=1, col=2)
grafica16.add_trace(go.Scatter(x=finact1.index, y=finact1["EPUMONETARY"], name="Economic Policy Uncertainty Index: Categorical Index: Monetary policy", line=dict(dash='dot', color='darkblue')), row=1, col=2)
grafica16.add_trace(go.Scatter(x=finact1.index, y=finact1["EPUGOVTSPEND"], name="Economic Policy Uncertainty Index: Categorical Index: Government spending", line=dict(dash='dot', color ='orangered')), row=1, col=2)
grafica16.add_trace(go.Scatter(x=finact1.index, y=finact1["EMVOVERALLEMV"], name="Equity Market Volatility Tracker: Overall (Right)", line=dict(color='red')), secondary_y=True, row=1, col=2)


grafica16.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica16.update_layout(dragmode='pan')

grafica16.show()

In [63]:
#GRAFICA 17 U.S. Treasury Yield Curve 
grafica17 = go.Figure()

# Agregar cada serie al gráfico
for i, column in enumerate(YieldCurve.columns):
    dash_type = 'dash' if i < 3 else 'solid'  # Establecer el tipo de línea según el índice
    text_position = 'top center' if i == len(YieldCurve.columns) - 1 else None  # Establecer la posición del texto
    grafica17.add_trace(go.Scatter(
        x=YieldCurve.index,
        y=YieldCurve[column],
        name=str(column),
        line=dict(dash=dash_type),  # Establecer el tipo de línea
        text=YieldCurve[column] if i == len(YieldCurve.columns) - 1 else None,  # Mostrar valores solo en la última serie
        mode='lines+markers+text' if i == len(YieldCurve.columns) - 1 else 'lines+markers',  # Modo de visualización de la serie
        textposition=text_position  # Posición del texto
    ))

# Personalizar el diseño del gráfico
grafica17.update_layout(
    title='U.S. Treasury Yield Curve Spot Rate',
    xaxis_title='Maturity',
    yaxis_title='Interest Rate',
    legend_title='Fecha'
)

grafica17.update_layout(dragmode='pan')
# Mostrar el gráfico
grafica17.show()


In [64]:
#Grafica 18 Financial Conditions Indices OJO ESTAN ESTANDARIZADOS 
#DIVIDIR RESPECTO A UN VALOR EN EL TIEMPO.MEJOR DIFERENCIA DE RETORNOS A 20 DÍAS. PARA ABAS GRAFICAS 
#TAL VEZ NO ES NECESARIO PONER EL VIX
grafica18 = make_subplots(rows=1, cols=2,specs=[[{"secondary_y": True}, {"secondary_y": True}]], subplot_titles=("Stock Market", "Bonds Market"), column_widths=[0.6, 0.4])

# Configure the title 
grafica18.update_layout(title="Financial Markets")

# Agregar título al eje Y 
grafica18.update_yaxes(title="Index (2020 = 100)", row=1, col=1)
grafica18.update_yaxes(title="Index(2020 = 100)", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica18.update_xaxes(range=[stocks.index[-900], stocks.index[-1]], row=1, col=1)
grafica18.update_xaxes(range=[stocks.index[-900], stocks.index[-1]], row=1, col=2)

min_y1 = min(stocks[["SP500", "DJIA", "NASDAQCOM"]].iloc[-900:].min() -10 )
max_y1 = max(stocks[["SP500", "DJIA", "NASDAQCOM"]].iloc[-900:].max() +10)
grafica18.update_yaxes(fixedrange=False, range=[min_y1, max_y1], row=1, col=1, secondary_y = False)



# Ajustar rango del eje Y para la segunda subgráfica
min_y2 = min(stocks[["US High Yield Index Total Return", "1-3 Year US Corporate Index Total Return"]].iloc[-900:].min() - 10)
max_y2 = max(stocks[["US High Yield Index Total Return", "1-3 Year US Corporate Index Total Return"]].iloc[-900:].max() + 10)
grafica18.update_yaxes(fixedrange=False, range=[min_y2, max_y2], row=1, col=2, secondary_y = False)


grafica18.update_yaxes(fixedrange=False)


# Add the three time series lines to the first graph
#grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["VIX"], name="VIX Standardized (Right)", line=dict(dash='solid', width=.8)), secondary_y=True, row=1, col=1)
grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["SP500"], name="S&P 500", line=dict(dash='solid', width=1.2)), row=1, col=1)
grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["DJIA"], name="Dow Jones Industrial Average", line=dict(dash='solid', width=1.2)), row=1, col=1)
grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["NASDAQCOM"], name="NASDAQ Composite Index", line=dict(dash='solid', width=1.2)), row=1, col=1)
# Valor donde quieres trazar la línea horizontal
valor_horizontal = 100
linea_horizontal = np.zeros(len(stocks)) + valor_horizontal
grafica18.add_trace(go.Scatter(x=stocks.index, y=linea_horizontal, line=dict(color='black', width=0.40), showlegend=False), row=1, col=1)


grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["US High Yield Index Total Return"], name="US High Yield Index Total Return"), row=1, col=2)
grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["1-3 Year US Corporate Index Total Return"], name="1-3 Year US Corporate Index Total Return"), row=1, col=2)
grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["CCC & Lower US High Yield Index Total Return"], name="CCC & Lower US High Yield Index Total Return"), row=1, col=2)
grafica18.add_trace(go.Scatter(x=stocks.index, y=stocks["Emerging Markets Corporate Plus Index Total Return"], name="Emerging Markets Corporate Plus Index Total Return"), row=1, col=2)
grafica18.add_trace(go.Scatter(x=stocks.index, y=linea_horizontal, line=dict(color='black', width=0.40), showlegend=False), row=1, col=2)

grafica18.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica18.update_layout(dragmode='pan')

grafica18.show()

In [65]:
#Grafica 19 Forward Rates and Term Premiums 
#PUEDE SER QUINCENAL O SEMANAL VERIFICAR ESO, PORQUE ESTÁ EN MENSUAL LA SEGUNDA GRAFICA 
grafica19 = make_subplots(rows=1, cols=2, subplot_titles=("Forward Rate: Market-Based Expectations of Monetary Policy Movements", "Term Premium on a 10 Year Zero Coupon Bond"))

# Configure the title 
grafica19.update_layout(title="Forward Rate and Term Premium")

# Agregar título al eje Y 
grafica19.update_yaxes(title="Rate", row=1, col=1)
grafica19.update_yaxes(title="Rate", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica19.update_xaxes(range=[FedFunds.index[-700], FedFunds.index[-1]], row=1, col=1)
grafica19.update_xaxes(range=[TermPremium.index[-24], TermPremium.index[-1]], row=1, col=2)

min_y1 = min(FedFunds[["3-month forward rate, 3 months ahead","Fed Funds Target Range - Upper Limit"]].iloc[-700:].min() -1 )
max_y1 = max(FedFunds[["3-month forward rate, 3 months ahead","Fed Funds Target Range - Lower Limit" ]].iloc[-700:].max() +1 )
grafica19.update_yaxes(fixedrange=False, range=[min_y1, max_y1], row=1, col=1)


grafica19.update_yaxes(fixedrange=False, row=1, col=2)

# Add the three time series lines to the first graph
grafica19.add_trace(go.Scatter(x=FedFunds.index, y=FedFunds["3-month forward rate, 3 months ahead"], name="3-month forward rate, 3 months ahead", line=dict(dash='solid')), row=1, col=1)
grafica19.add_trace(go.Scatter(x=FedFunds.index, y=FedFunds["Fed Funds Target Range - Upper Limit"], name="Fed Funds Target Range - Upper Limit"), row=1, col=1)
grafica19.add_trace(go.Scatter(x=FedFunds.index, y=FedFunds["Fed Funds Target Range - Lower Limit"], name="Fed Funds Target Range - Lower Limit"), row=1, col=1)



grafica19.add_trace(go.Scatter(x=TermPremium.index, y=TermPremium["U.S. Treasury Securities at 10-Year"], name="U.S. Treasury Securities at 10-Year"), row=1, col=2)
grafica19.add_trace(go.Scatter(x=TermPremium.index, y=TermPremium["Term Premium on a 10 Year"], name="Term Premium on a 10 Year", showlegend=False), row=1, col=2)
grafica19.add_trace(go.Bar(x=TermPremium.index, y=TermPremium["Term Premium on a 10 Year"], name="Term Premium on a 10 Year", offsetgroup=0, marker_color="gold"), row=1, col=2)
grafica19.add_trace(go.Bar(x=TermPremium.index, y=TermPremium["Average expected short rate"], name="Average expected short rate", offsetgroup=0), row=1, col=2)
grafica19.update_layout(barmode='relative')


grafica19.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica19.update_layout(dragmode='pan')

grafica19.show()


In [66]:
#Grafica 20 Federal Reserve Balance Sheet 
#OJO FALTA PONER QUE LOS LIABILITIES SE PRESENTAN COMO NEGATIVO, TAMBIEN FALTA AJUSTAL LA PALETA DE COLORES PARA QUE NO SE REPITAN
#falta poner un recuadro de texto en la grafica que en positivo sea assets y negativo sea liabilities ocmo en la imagen
#HACER UNA GRAFICA PARA LOS CAMBIOS MENSUALES DE CADA RUBRO,.
grafica20 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica20.update_layout(
    title="Quantitative Easing: Federal Reserve Balance Sheet",
    xaxis_title="Fecha",
    yaxis_title="Millions of Dollars",
    plot_bgcolor="white"
)

# Configurar el rango del eje x para los últimos 3 años
grafica20.update_layout(xaxis_range=[FedBalance.index[-120], FedBalance.index[-1]])


# Añadir las tres líneas de la serie de tiempo
grafica20.add_trace(go.Scatter(x=FedBalance.index, y=FedBalance["Total Assets"], name="Total Assets",showlegend=False))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=FedBalance["U.S. Treasury Securities"], name="U.S. Treasury Securities", offsetgroup=0))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=FedBalance["Mortgage-Backed Securities"], name="Mortgage-Backed Securities", offsetgroup=0))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=FedBalance["Repo, Swaps, Credit and Liquidity Facilities"], name="Repo, Swaps, Credit and Liquidity Facilities", offsetgroup=0))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=FedBalance["Other Assets"], name="Other Assets", offsetgroup=0))

zero_line = np.zeros(len(FedBalance))
grafica20.add_trace(go.Scatter(x=FedBalance.index, y=zero_line, line=dict(color='black', width=1.2), showlegend=False))

grafica20.add_trace(go.Scatter(x=FedBalance.index, y=-FedBalance["Total Liabilities"], name="Total Liabilities",showlegend=False))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=-FedBalance["Federal Reserve Notes"], name="Federal Reserve Notes", offsetgroup=0))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=-FedBalance["Deposits Held by Depository Institutions (Reserves)"], name="Deposits Held by Depository Institutions (Reserves)", offsetgroup=0))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=-FedBalance["Reverse Repurchase Agreements"], name="Reverse Repurchase Agreements", offsetgroup=0))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=-FedBalance["U.S. Treasury, General Account (TGA)"], name="U.S. Treasury, General Account (TGA)", offsetgroup=0))
grafica20.add_trace(go.Bar(x=FedBalance.index, y=-FedBalance["Other Liabilities"], name="Other Liabilities", offsetgroup=0))


grafica20.update_layout(barmode='relative')
grafica20.update_xaxes(rangeslider_visible=True)
grafica20.update_yaxes(fixedrange=False, autorange=True)
grafica20.update_layout(dragmode='pan')




# Mostrar la figura
grafica20.show()

In [67]:
grafica21 = make_subplots(rows=1, cols=2, subplot_titles=("U.S. Treasury Securities Holders, Market Value Levels", "Market Share of each Sector"))

## Configure the title 
grafica21.update_layout(title="U.S. Treasury Securities Holders")

# Agregar título al eje Y de la primera subgráfica
grafica21.update_yaxes(title="Millions of dollars", row=1, col=1)

# Agregar título al eje Y de la segunda subgráfica
grafica21.update_yaxes(title="Porcent", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica21.update_xaxes(range=[Treasury.index[-36], Treasury.index[-1]], row=1, col=1)

# Configurar el rango del eje x para los últimos 3 años en la segunda subgráfica
grafica21.update_xaxes(range=[Treasury.index[-36], Treasury.index[-1]], row=1, col=2)

grafica21.update_yaxes(fixedrange=False, row=1, col=1)

grafica21.update_yaxes(fixedrange=False, row=1, col=2)

# Enable x-axis range slider for both graphs
grafica21.update_xaxes(rangeslider_visible=True)

# Ajustar margen inferior para dejar espacio para la anotación
grafica21.update_layout(margin=dict(b=123))

# Añadir las tres líneas de la serie de tiempo
grafica21.add_trace(go.Scatter(x=Treasury.index, y=Treasury["Treasury Levels"], name="Treasury Levels",showlegend=False), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Monetary Authority"], name="Monetary Authority", offsetgroup=0), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Rest of the World"], name="Rest of the World", offsetgroup=0, marker_color='darkblue'), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Household sector"], name="Household sector", offsetgroup=0), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Other nonfinancial"], name="Other nonfinancial", offsetgroup=0), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Banks"], name="Banks", offsetgroup=0), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Money Market Funds"], name="Money Market Funds", offsetgroup=0), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Mutual Funds"], name="Mutual Funds", offsetgroup=0, marker_color='pink'), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Shadow Banking"], name="Shadow Banking", offsetgroup=0, marker_color = 'lightcoral'), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Insurance and pensions"], name="Insurance and pensions", offsetgroup=0), row=1, col=1)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["GSEs"], name="GSEs", offsetgroup=0), row=1, col=1)
grafica21.update_layout(barmode='relative')

grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Monetary Authority"]/Treasury['Treasury Levels'], name="Monetary Authority", offsetgroup=0, showlegend=False), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Rest of the World"]/Treasury['Treasury Levels'], name="Rest of the World", offsetgroup=0,showlegend=False, marker_color='darkblue'), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Household sector"]/Treasury['Treasury Levels'], name="Household sector", offsetgroup=0, showlegend=False), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Other nonfinancial"]/Treasury['Treasury Levels'], name="Other nonfinancial", offsetgroup=0, showlegend=False), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Banks"]/Treasury['Treasury Levels'], name="Banks", offsetgroup=0,showlegend=False), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Money Market Funds"]/Treasury['Treasury Levels'], name="Money Market Funds", offsetgroup=0,showlegend=False), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Mutual Funds"]/Treasury['Treasury Levels'], name="Mutual Funds", offsetgroup=0,showlegend=False, marker_color='pink'), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Shadow Banking"]/Treasury['Treasury Levels'], name="Shadow Banking", offsetgroup=0,showlegend=False, marker_color = 'lightcoral'), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["Insurance and pensions"]/Treasury['Treasury Levels'], name="Insurance and pensions", offsetgroup=0,showlegend=False), row=1, col=2)
grafica21.add_trace(go.Bar(x=Treasury.index, y=Treasury["GSEs"]/Treasury['Treasury Levels'], name="GSEs", offsetgroup=0,showlegend=False), row=1, col=2)
grafica21.update_layout(barmode='relative')

grafica21.update_xaxes(rangeslider_visible=True)
grafica21.update_yaxes(fixedrange=False, autorange=True)
grafica21.update_layout(dragmode='pan')


# Mostrar la figura
grafica21.show()

In [68]:
grafica22 = make_subplots(rows=1, cols=2, subplot_titles=("Quarterly Change, Market Value", "Quarterly Net Purchases"))

## Configure the title 
grafica22.update_layout(title="U.S. Treasury Securities Holders")

# Agregar título al eje Y de la primera subgráfica
grafica22.update_yaxes(title="Millions of dollars", row=1, col=1)

# Agregar título al eje Y de la segunda subgráfica
grafica22.update_yaxes(title="Millions of dollars", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica22.update_xaxes(range=[Treasury1.index[-16], Treasury1.index[-1]], row=1, col=1)

# Configurar el rango del eje x para los últimos 3 años en la segunda subgráfica
grafica22.update_xaxes(range=[Treasury2.index[-16], Treasury2.index[-1]], row=1, col=2)

grafica22.update_yaxes(fixedrange=False, row=1, col=1)

grafica22.update_yaxes(fixedrange=False, row=1, col=2)

# Enable x-axis range slider for both graphs
grafica22.update_xaxes(rangeslider_visible=True)

# Ajustar margen inferior para dejar espacio para la anotación
grafica22.update_layout(margin=dict(b=123))

# Añadir las tres líneas de la serie de tiempo
grafica22.add_trace(go.Scatter(x=Treasury1.index, y=Treasury1["Treasury Transactions"], name="Treasury Transactions",showlegend=False, line=dict(width =1)), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["Monetary Authority"], name="Monetary Authority", offsetgroup=0, marker_color='OrangeRed'), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["Rest of the World"], name="Rest of the World", offsetgroup=0, marker_color='darkblue'), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["Household sector"], name="Household sector", offsetgroup=0, marker_color='MediumPurple'), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["Other nonfinancial"], name="Other nonfinancial", offsetgroup=0, marker_color='orange'), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["Banks"], name="Banks", offsetgroup=0, marker_color='aqua'), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["Shadow Banking"], name="Shadow Banking", offsetgroup=0, marker_color = 'Salmon'), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["Insurance and pensions"], name="Insurance and pensions", offsetgroup=0, marker_color = 'gold'), row=1, col=1)
grafica22.add_trace(go.Bar(x=Treasury1.index, y=Treasury1["GSEs"], name="GSEs", offsetgroup=0, marker_color = 'MediumSlateBlue'), row=1, col=1)
grafica22.update_layout(barmode='relative')

grafica22.add_trace(go.Scatter(x=Treasury2.index, y=Treasury2["Treasury Transactions"], name="Treasury Transactions",showlegend=False, line=dict(width =1, color = 'MediumSlateBlue')), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["Monetary Authority"], name="Monetary Authority", offsetgroup=0, marker_color='OrangeRed',showlegend=False), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["Rest of the World"], name="Rest of the World", offsetgroup=0, marker_color='darkblue',showlegend=False), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["Household sector"], name="Household sector", offsetgroup=0, marker_color='MediumPurple',showlegend=False), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["Other nonfinancial"], name="Other nonfinancial", offsetgroup=0, marker_color='orange',showlegend=False), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["Banks"], name="Banks", offsetgroup=0, marker_color='aqua',showlegend=False), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["Shadow Banking"], name="Shadow Banking", offsetgroup=0, marker_color = 'Salmon',showlegend=False), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["Insurance and pensions"], name="Insurance and pensions", offsetgroup=0, marker_color = 'gold',showlegend=False), row=1, col=2)
grafica22.add_trace(go.Bar(x=Treasury2.index, y=Treasury2["GSEs"], name="GSEs", offsetgroup=0, marker_color = 'MediumSlateBlue',showlegend=False), row=1, col=2)
grafica22.update_layout(barmode='relative')

grafica22.update_xaxes(rangeslider_visible=True)
grafica22.update_yaxes(fixedrange=False, autorange=True)
grafica22.update_layout(dragmode='pan')


# Mostrar la figura
grafica22.show()

In [69]:
#Grafica 23 Debt Outstanding by Intrument and Loans by Instruments QUARTERLY LEVELS
grafica23 = make_subplots(rows=1, cols=2, subplot_titles=("Quarterly Levels, Market Value", "Market Share"))

# Configurar el título y los títulos de los ejes x e y
grafica23.update_layout(
    title="U.S. Debt Outstanding and Loans by Intrument. Quarterly Levels",
    xaxis_title="Fecha",
    yaxis_title="Millions of dollars",
    plot_bgcolor="white"
)

# Configurar el rango del eje x para los últimos 3 años
grafica23.update_layout(xaxis_range=[Debt.index[-64], Debt.index[-1]])

# Ajustar margen inferior para dejar espacio para la anotación
grafica23.update_layout(margin=dict(b=123))


# Añadir las tres líneas de la serie de tiempo
grafica23.add_trace(go.Line(x=Debt.index, y=Debt["Total Loans"], name="Total Loans", showlegend = False, marker_color = "mediumseagreen"), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Loans N.E.C."], name="Loans N.E.C.", marker_color='grey', offsetgroup=0), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Other Loans and Advances"], name="Other Loans and Advances", marker_color='darkblue', offsetgroup=0), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Mortgages"], name="Mortgages", marker_color='lightskyblue', offsetgroup=0), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Consumer Credit"], name="Consumer Credit", offsetgroup=0, marker_color='tomato'), row=1, col=1)

grafica23.add_trace(go.Line(x=Debt.index, y=Debt["Total Debt"], name="Total Debt", showlegend = False), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Open Market Paper"], name="Open Market Paper", offsetgroup=0, marker_color = 'hotpink'), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Treasury Securities"], name="Treasury Securities", offsetgroup=0, marker_color = 'gold'), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["U.S. Government Agency Securities"], name="U.S. Government Agency Securities", offsetgroup=0, marker_color = 'green'), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Municipal Securities"], name="Municipal Securities", offsetgroup=0, marker_color='mediumorchid'), row=1, col=1)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Corporate and Foreign Bonds"], name="Corporate and Foreign Bonds", offsetgroup=0, marker_color='mediumslateblue'), row=1, col=1)


grafica23.add_trace(go.Line(x=Debt.index, y=Debt["Total Debt and Loans"], name="Total Debt and Loans", marker_color ='orangered', showlegend = False), row=1, col=1)
grafica23.update_layout(barmode='relative')

# Añadir las tres líneas de la serie de tiempo
grafica23.add_trace(go.Line(x=Debt.index, y=Debt["Total Loans"]/Debt["Total Debt and Loans"], name="Total Loans", showlegend = False, marker_color = "mediumseagreen"), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Loans N.E.C."]/Debt["Total Debt and Loans"], name="Loans N.E.C.", marker_color='grey', offsetgroup=0), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Other Loans and Advances"]/Debt["Total Debt and Loans"], name="Other Loans and Advances", marker_color='darkblue', offsetgroup=0), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Mortgages"]/Debt["Total Debt and Loans"], name="Mortgages", marker_color='lightskyblue', offsetgroup=0), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Consumer Credit"]/Debt["Total Debt and Loans"], name="Consumer Credit", offsetgroup=0, marker_color='tomato'), row=1, col=2)

grafica23.add_trace(go.Line(x=Debt.index, y=Debt["Total Debt"]/Debt["Total Debt and Loans"], name="Total Debt", showlegend = False, marker_color = 'coral'), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Open Market Paper"]/Debt["Total Debt and Loans"], name="Open Market Paper", offsetgroup=0, marker_color = 'hotpink'), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Treasury Securities"]/Debt["Total Debt and Loans"], name="Treasury Securities", offsetgroup=0, marker_color = 'gold'), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["U.S. Government Agency Securities"]/Debt["Total Debt and Loans"], name="U.S. Government Agency Securities", offsetgroup=0, marker_color = 'green'), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Municipal Securities"]/Debt["Total Debt and Loans"], name="Municipal Securities", offsetgroup=0, marker_color='mediumorchid'), row=1, col=2)
grafica23.add_trace(go.Bar(x=Debt.index, y=Debt["Corporate and Foreign Bonds"]/Debt["Total Debt and Loans"], name="Corporate and Foreign Bonds", offsetgroup=0, marker_color='mediumslateblue'), row=1, col=2)


grafica23.add_trace(go.Line(x=Debt.index, y=Debt["Total Debt and Loans"], name="Total Debt and Loans", marker_color ='orangered', showlegend = False))

grafica23.update_layout(barmode='relative')





grafica23.update_xaxes(rangeslider_visible=True)
grafica23.update_yaxes(fixedrange=False, autorange=True)
grafica23.update_layout(dragmode='pan')


# Mostrar la figura
grafica23.show()

D:\devenv\Anaconda32022.05\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [70]:
#Grafica 24 Debt Outstanding by Intrument and Loans by Instruments QUARTERLY LEVELS, CHANGE
grafica24 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica24.update_layout(
    title="Change in U.S. Debt Outstanding and Loans by Intrument. Quarterly Levels",
    xaxis_title="Fecha",
    yaxis_title="Millions of Dollars",
    plot_bgcolor="white"
)

# Configurar el rango del eje x para los últimos 3 años
grafica24.update_layout(xaxis_range=[Debt1.index[-24], Debt1.index[-1]])

# Ajustar margen inferior para dejar espacio para la anotación
grafica24.update_layout(margin=dict(b=123))


# Añadir las tres líneas de la serie de tiempo
grafica24.add_trace(go.Line(x=Debt1.index, y=Debt1["Total Loans"], name="Total Loans", showlegend = False))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Loans N.E.C."], name="Loans N.E.C.", marker_color='lightgrey', offsetgroup=0))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Other Loans and Advances"], name="Other Loans and Advances", marker_color='darkblue', offsetgroup=0))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Mortgages"], name="Mortgages", marker_color='lightskyblue', offsetgroup=0))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Consumer Credit"], name="Consumer Credit", offsetgroup=0))

grafica24.add_trace(go.Line(x=Debt1.index, y=Debt1["Total Debt"], name="Total Debt", showlegend = False))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Open Market Paper"], name="Open Market Paper", offsetgroup=0))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Treasury Securities"], name="Treasury Securities", offsetgroup=0))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["U.S. Government Agency Securities"], name="U.S. Government Agency Securities", offsetgroup=0))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Municipal Securities"], name="Municipal Securities", offsetgroup=0))
grafica24.add_trace(go.Bar(x=Debt1.index, y=Debt1["Corporate and Foreign Bonds"], name="Corporate and Foreign Bonds", offsetgroup=0))


grafica24.add_trace(go.Line(x=Debt1.index, y=Debt1["Total Debt and Loans"], name="Total Debt and Loans", marker_color ='orangered', showlegend = False))

grafica24.update_layout(barmode='relative')
grafica24.update_xaxes(rangeslider_visible=True)
grafica24.update_yaxes(fixedrange=False, autorange=True)
grafica24.update_layout(dragmode='pan')


# Mostrar la figura
grafica24.show()

In [71]:
#Grafica 25 Debt Outstanding by Intrument and Loans by Instruments QUARTERLY LEVELS, CHANGE
grafica25 = go.Figure()

# Configurar el título y los títulos de los ejes x e y
grafica25.update_layout(
    title="Change in U.S. Debt Outstanding and Loans by Intrument. Quarterly Levels",
    xaxis_title="Fecha",
    yaxis_title="Millions of Dollars"
)

# Configurar el rango del eje x para los últimos 3 años
grafica25.update_layout(xaxis_range=[Debt2.index[-24], Debt2.index[-1]])

# Ajustar margen inferior para dejar espacio para la anotación
grafica25.update_layout(margin=dict(b=123))


# Añadir las tres líneas de la serie de tiempo
grafica25.add_trace(go.Line(x=Debt2.index, y=Debt2["Total Loans"], name="Total Loans", showlegend = False))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Loans N.E.C."], name="Loans N.E.C.", marker_color='lightgrey', offsetgroup=0))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Other Loans and Advances"], name="Other Loans and Advances", marker_color='darkblue', offsetgroup=0))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Mortgages"], name="Mortgages", marker_color='lightskyblue', offsetgroup=0))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Consumer Credit"], name="Consumer Credit", offsetgroup=0))

grafica25.add_trace(go.Line(x=Debt2.index, y=Debt2["Total Debt"], name="Total Debt", showlegend = False))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Open Market Paper"], name="Open Market Paper", offsetgroup=0))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Treasury Securities"], name="Treasury Securities", offsetgroup=0))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["U.S. Government Agency Securities"], name="U.S. Government Agency Securities", offsetgroup=0))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Municipal Securities"], name="Municipal Securities", offsetgroup=0))
grafica25.add_trace(go.Bar(x=Debt2.index, y=Debt2["Corporate and Foreign Bonds"], name="Corporate and Foreign Bonds", offsetgroup=0))

grafica25.update_layout(barmode='relative')
grafica25.update_xaxes(rangeslider_visible=True)
grafica25.update_yaxes(fixedrange=False, autorange=True)
grafica25.update_layout(dragmode='pan')


# Mostrar la figura
grafica25.show()

In [72]:
#GRAFICA 26 U.S. Treasury Yield Curve 
#FALTA PREGUNTAR A CUANTOS MESES LES GUSTARÍA VERLA
grafica26 = go.Figure()

# Agregar cada serie al gráfico
for i, column in enumerate(HQMBond.columns):
    dash_type = 'dot' if i < 3 else 'solid'  # Establecer el tipo de línea según el índice
    text_position = 'top center' if i == len(HQMBond.columns) - 1 else None  # Establecer la posición del texto
    grafica26.add_trace(go.Scatter(
        x=HQMBond.index,
        y=HQMBond[column],
        name=str(column),
        line=dict(dash=dash_type),  # Establecer el tipo de línea
        text=HQMBond[column] if i == len(HQMBond.columns) - 1 else None,  # Mostrar valores solo en la última serie
        mode='lines + markers' if i == len(HQMBond.columns) - 1 else 'lines',  # Modo de visualización de la serie
        textposition=text_position  # Posición del texto
    ))

# Personalizar el diseño del gráfico
grafica26.update_layout(
    title='High Quality Market (HQM) Corporate Bond Spot Yield Curve',
    xaxis_title='Maturity',
    yaxis_title='Interest Rate',
    legend_title='Fecha'
)

grafica26.update_layout(dragmode='pan')
# Mostrar el gráfico
grafica26.show()

In [73]:
#GRAFICA 27 Credit Market 
grafica27 = make_subplots(rows=1, cols=2, subplot_titles=("Household Debt Service Ratio", "Consumer Credit Debt Ratio"))

# Agregar título al eje Y 
grafica27.update_yaxes(title="(In percent of disposable income)", row=1, col=1)
grafica27.update_yaxes(title="(In percent of disposable income)", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica27.update_xaxes(range=[Debtservice.index[-41], Debtservice.index[-1]], row=1, col=1)
grafica27.update_xaxes(range=[DebtRatio.index[-41], DebtRatio.index[-1]], row=1, col=2)
grafica27.update_yaxes(fixedrange=False)


# Ajustar margen inferior para dejar espacio para la anotación
grafica27.update_layout(margin=dict(b=123))

# Add the three time series lines to the first graph
grafica27.add_trace(go.Scatter(x=Debtservice.index, y=Debtservice['Household Debt Service'], name="Household Debt Service (A+B)", marker_color = 'lightskyblue'), row=1, col=1)
grafica27.add_trace(go.Scatter(x=Debtservice.index, y=Debtservice["Consumer Debt Service"], name="A. Consumer Debt Service"), row=1, col=1)
grafica27.add_trace(go.Scatter(x=Debtservice.index, y=Debtservice["Mortgage Debt Service"], name="B. Mortgage Debt Service"), row=1, col=1)

grafica27.add_trace(go.Scatter(x=DebtRatio.index, y=DebtRatio["Credit Card Debt"], name="Credit Card Debt"), row=1, col=2)
grafica27.add_trace(go.Scatter(x=DebtRatio.index, y=DebtRatio["Auto Loans"], name="Auto Loans"), row=1, col=2)
grafica27.add_trace(go.Scatter(x=DebtRatio.index, y=DebtRatio["Student Loans"], name="Student Loans"), row=1, col=2)

grafica27.update_xaxes(rangeslider_visible=True)
# Update the y-axes and figure configuration
grafica27.update_layout(dragmode='pan')

grafica27.show()

In [76]:
grafica28 = make_subplots(rows=1, cols=2, subplot_titles=("U.S. Corporate and Foreign Bonds Holders, Market Value Levels", "Market Share of each Sector"))

## Configure the title 
grafica28.update_layout(title="U.S. Corporate and Foreign Bonds Holders ( includes Commercial Paper)")

# Agregar título al eje Y de la primera subgráfica
grafica28.update_yaxes(title="Millions of dollars", row=1, col=1)

# Agregar título al eje Y de la segunda subgráfica
grafica28.update_yaxes(title="Porcent", row=1, col=2)

# Configurar el rango del eje x para los últimos 3 años en la primera subgráfica
grafica28.update_xaxes(range=[CorporateBonds.index[-64], CorporateBonds.index[-1]], row=1, col=1)

# Configurar el rango del eje x para los últimos 3 años en la segunda subgráfica
grafica28.update_xaxes(range=[CorporateBonds.index[-64], CorporateBonds.index[-1]], row=1, col=2)

grafica28.update_yaxes(fixedrange=False, row=1, col=1)

grafica28.update_yaxes(fixedrange=False, row=1, col=2)

# Enable x-axis range slider for both graphs
grafica28.update_xaxes(rangeslider_visible=True)

# Ajustar margen inferior para dejar espacio para la anotación
grafica28.update_layout(margin=dict(b=123))

# Añadir las tres líneas de la serie de tiempo
grafica28.add_trace(go.Scatter(x=CorporateBonds.index, y=CorporateBonds["Total"], name="Total",showlegend=False, marker_color='gray'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Fed. Govt."], name="Fed. Govt.", offsetgroup=0), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Rest of the World"], name="Rest of the World", offsetgroup=0, marker_color='darkblue'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Household Sector"], name="Household Sector", offsetgroup=0, marker_color='orange'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Other nonfinancial"], name="Other nonfinancial", offsetgroup=0, marker_color='lightblue'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Banks"], name="Banks", offsetgroup=0, marker_color='seagreen'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Money Market Funds"], name="Money Market Funds", offsetgroup=0, marker_color='hotpink'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Mutual Funds"], name="Mutual Funds", offsetgroup=0, marker_color='pink'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Shadow Banking"], name="Shadow Banking", offsetgroup=0, marker_color = 'lightcoral'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Insurance and pensions"], name="Insurance and pensions", offsetgroup=0, marker_color = 'gold'), row=1, col=1)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["GSEs"], name="GSEs", offsetgroup=0, marker_color = 'rebeccapurple'), row=1, col=1)
grafica28.update_layout(barmode='relative')

grafica28.add_trace(go.Scatter(x=CorporateBonds.index, y=CorporateBonds["Total"]/CorporateBonds["Total"], name="Total",showlegend=False, marker_color='gray'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Fed. Govt."]/CorporateBonds['Total'], name="Fed. Govt.", offsetgroup=0, showlegend=False), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Rest of the World"]/CorporateBonds['Total'], name="Rest of the World", offsetgroup=0,showlegend=False, marker_color='darkblue'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Household Sector"]/CorporateBonds['Total'], name="Household sector", offsetgroup=0, showlegend=False, marker_color='orange'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Other nonfinancial"]/CorporateBonds['Total'], name="Other nonfinancial", offsetgroup=0, showlegend=False, marker_color='lightblue'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Banks"]/CorporateBonds['Total'], name="Banks", offsetgroup=0,showlegend=False, marker_color='seagreen'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Money Market Funds"]/CorporateBonds['Total'], name="Money Market Funds", offsetgroup=0,showlegend=False, marker_color='hotpink'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Mutual Funds"]/CorporateBonds['Total'], name="Mutual Funds", offsetgroup=0,showlegend=False, marker_color='pink'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Shadow Banking"]/CorporateBonds['Total'], name="Shadow Banking", offsetgroup=0,showlegend=False, marker_color = 'lightcoral'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["Insurance and pensions"]/CorporateBonds['Total'], name="Insurance and pensions", offsetgroup=0,showlegend=False, marker_color = 'gold'), row=1, col=2)
grafica28.add_trace(go.Bar(x=CorporateBonds.index, y=CorporateBonds["GSEs"]/CorporateBonds['Total'], name="GSEs", offsetgroup=0,showlegend=False, marker_color = 'rebeccapurple'), row=1, col=2)
grafica28.update_layout(barmode='relative')

grafica28.update_xaxes(rangeslider_visible=True)
grafica28.update_yaxes(fixedrange=False, autorange=True)
grafica28.update_layout(dragmode='pan')


# Mostrar la figura
grafica28.show()
#grafica28.write_html("Grafica28.html")

In [78]:
with open('Variables Económicas US.html', 'w', encoding='utf-8') as f:
    f.write('<h1 style="text-align: center; color: black; font-size: 22px; font-family: Arial, sans-serif;">Variables Económicas US</h1>')
    
    f.write('<figure>')
    f.write(grafica1.to_html(full_html=True, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">A zero value for the index indicates that the national economy is expanding at its historical trend rate of growth; \
    <br> negative values indicate below-average growth and positive values indicate above-average growth.</figcaption>')
    f.write('</figure>')
    
    f.write('<figure>')
    f.write(grafica2.to_html(full_html=True, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Sticky Price: Because these goods and services change price relatively infrequently, they are thought to incorporate expectations about future inflation to a greater degree than prices that change on a more frequent basis.\
    <br> The 5Y/5Y forward uses the difference in market interest rates for a period of 5 years, beginning 5 years in the future.</figcaption>')
    f.write('</figure>')
    
    f.write('<figure>')
    f.write(grafica3.to_html(full_html=True, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Quarterly. Seasonally Adjusted Annual Rate <br> GDPNow is a nowcasting model for gross domestic product (GDP) growth that synthesizes the bridge equation approach relating \
    <br> GDP subcomponents to monthly source data with factor model and Bayesian vector autoregression approaches.</figcaption>')
    f.write('</figure>')
    
    f.write('<figure>')
    f.write(grafica4.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Real potential GDP is the CBO’s estimate of the output the economy would produce with a high rate of use of its capital and labor resources.\
    <br> The data is adjusted to remove the effects of inflation.</figcaption>')
    f.write('</figure>')
    
    f.write('<br>')
    f.write(grafica5.to_html(full_html=False, include_plotlyjs='cdn'))
    
    f.write('<figure>')
    f.write(grafica6.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Quarterly. Seasonally Adjusted.</figcaption>')
    f.write('</figure>')
    
    
    f.write('<figure>')
    f.write(grafica7.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Quarterly. Seasonally Adjusted.</figcaption>')
    f.write('</figure>')
    
    f.write('<figure>')
    f.write(grafica8.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Monthly. Seasonally Adjusted.</figcaption>')
    f.write('</figure>')
    
    f.write('<figure>')
    f.write(grafica9.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Monthly. Seasonally Adjusted Annual Rate.</figcaption>')
    f.write('</figure>')
    
    f.write('<figure>')
    f.write(grafica10.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Monthly. Seasonally Adjusted.</figcaption>')
    f.write('</figure>')
    
    f.write('<figure>')
    f.write(grafica11.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Monthly. Seasonally Adjusted.</figcaption>')
    f.write('</figure>')
    
    
    f.write(grafica12.to_html(full_html=False, include_plotlyjs='cdn'))
    
    f.write('<figure>')
    f.write(grafica13.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Quarterly. Seasonally Adjusted.</figcaption>')
    f.write('</figure>')
    
    
    f.write(grafica14.to_html(full_html=False, include_plotlyjs='cdn'))
            
    f.write('<figure>')        
    f.write(grafica15.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">Frequency: Quarterly, End of Period. Not Seasonally Adjusted.</figcaption>')
    f.write('</figure>')
    
    f.write('<br>')
    f.write('<h2 style="text-align: center; color: black; font-size: 22px; font-family: Arial, sans-serif;">Variables Financieras U.S.</h2>')
    
    f.write('<figure>') 
    f.write(grafica16.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">KCFSI is a monthly measure of stress in the U.S. financial system based on 11 financial market variables. \
    <br> A positive value indicates that financial stress is above the long-run average, while a negative value indicates the opposite.\
    <br> U.S. EPU is an index constructed based on newspaper articles regarding policy uncertainty from leading newspapers.</figcaption>')
    f.write('</figure>')
    
    f.write(grafica17.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write(grafica18.to_html(full_html=False, include_plotlyjs='cdn'))
    
    f.write('<figure>')
    f.write(grafica19.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">The 3-month forward rate, 3 months ahead can illustrate how financial markets anticipate monetary policy movements.\
    <br> The average expected short rate is calculated by difference.</figcaption>')
    f.write('</figure>')
    
    
    f.write(grafica20.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write(grafica21.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write(grafica22.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write(grafica23.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write(grafica24.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write(grafica25.to_html(full_html=False, include_plotlyjs='cdn'))
    
    f.write('<figure>')
    f.write(grafica26.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write('<figcaption style="text-align: left; color: grey; font-family: Arial, sans-serif;">The HQM yield curve uses data from a set of high quality corporate bonds rated AAA, AA, or A \
    <br> that accurately represent the high quality corporate bond market.</figcaption>')
    f.write('</figure>')
    
    
    f.write(grafica27.to_html(full_html=False, include_plotlyjs='cdn'))
    f.write(grafica28.to_html(full_html=False, include_plotlyjs='cdn'))